# <font color=red>DATA GATHERING I: MUSIC RELEASES AND THEIR GEOGRAPHICAL ORIGIN</font>

## <font color=blue>1) Artist information</font>

### Data from Musicbrainz.org

In [61]:
import pandas as pd
import numpy as np
import reverse_geocoder #pip install reverse geocoder in console
import time
#import tqdm

In [62]:
artists= pd.read_csv('Musicbrainz/Tables_used/artist.txt',sep='\t', header=None, engine='c', usecols=[0,1,2,11,17])
artists.columns = ['artist_id','artist_mbid','artist_name','start_area1', 'start_area2']
artists.head()

artist_id                           artist_mbid      artist_name  \
0     805192  8972b1c1-6482-4750-b51f-596d2edea8b1            WIK▲N   
1     371203  49add228-eac5-4de8-836c-d75cde7369c3      Pete Moutso   
2     273232  c112a400-af49-4665-8bba-741531d962a1          Zachary   
3     101060  ca3f3ee1-c4a7-4bac-a16a-0b888a396c6b  The Silhouettes   
4     145773  7b4a548e-a01a-49b7-82e7-b49efeb9732c     Aric Leavitt   

   start_area1  start_area2  
0          NaN          NaN  
1          NaN          NaN  
2          NaN          NaN  
3        222.0       7707.0  
4          NaN          NaN

In [63]:
#Let's see how many artists we have:
artists['artist_id'].nunique()

1476425

In [64]:
#How much info we have for each artist?
artists.isnull().sum(axis=0)

artist_id            0
artist_mbid          0
artist_name          8
start_area1     808442
start_area2    1274001
dtype: int64

What are the "start_area1" and "start_area2"? If we look at Musicbrainz's field description for each artist (https://musicbrainz.org/doc/Artist), we can see that:

Area: The artist area, as the name suggests, indicates the area with which an artist is primarily identified with. It is often, but not always, its birth/formation country.

We will keep this information as the artist's origin for later.

We need to incorporate as well the table called "artist credit", which gives us the artist credit_id. We will use this field to join later on each release with its artist:

In [65]:
artists_credit= pd.read_csv('Musicbrainz/Tables_used/artist_credit_name.txt',sep='\t', header=None, engine='c', usecols=[0,2,3])
artists_credit.columns = ['credit_id','artist_id','artist_name']
artists_credit.head()

credit_id  artist_id             artist_name
0     578352     578352           Gustav Ruppke
1     273232     273232                 Zachary
2     153193     153193  The High Level Ranters
3      32262      32262        Georges Brassens
4    1389968    1171184    Harvard of the South

In [66]:
#Let's join the artists with their credit id and verify that the matching is good:
df = pd.merge(artists, artists_credit, how='left', on='artist_id')
df.head()

artist_id                           artist_mbid    artist_name_x  \
0     805192  8972b1c1-6482-4750-b51f-596d2edea8b1            WIK▲N   
1     371203  49add228-eac5-4de8-836c-d75cde7369c3      Pete Moutso   
2     273232  c112a400-af49-4665-8bba-741531d962a1          Zachary   
3     101060  ca3f3ee1-c4a7-4bac-a16a-0b888a396c6b  The Silhouettes   
4     145773  7b4a548e-a01a-49b7-82e7-b49efeb9732c     Aric Leavitt   

   start_area1  start_area2  credit_id    artist_name_y  
0          NaN          NaN   822846.0            WIK▲N  
1          NaN          NaN        NaN              NaN  
2          NaN          NaN   273232.0          Zachary  
3        222.0       7707.0   101060.0  The Silhouettes  
4          NaN          NaN   145773.0     Aric Leavitt

In [67]:
#It looks like it makes sense. Please note that the credit id is sometimes equal to the artist_id, but not always:
df['check'] = df['artist_id'] - df['credit_id']
df['check'].nunique()

1270628

In [68]:
df.isnull().sum(axis=0)

artist_id              0
artist_mbid            0
artist_name_x         15
start_area1      1120376
start_area2      2109027
credit_id         461241
artist_name_y     461253
check             461241
dtype: int64

In [69]:
#We can now get rid of check and the duplicate artist_name column:
df.drop(labels=['check','artist_name_y'], axis=1, inplace=True)
df.head()

artist_id                           artist_mbid    artist_name_x  \
0     805192  8972b1c1-6482-4750-b51f-596d2edea8b1            WIK▲N   
1     371203  49add228-eac5-4de8-836c-d75cde7369c3      Pete Moutso   
2     273232  c112a400-af49-4665-8bba-741531d962a1          Zachary   
3     101060  ca3f3ee1-c4a7-4bac-a16a-0b888a396c6b  The Silhouettes   
4     145773  7b4a548e-a01a-49b7-82e7-b49efeb9732c     Aric Leavitt   

   start_area1  start_area2  credit_id  
0          NaN          NaN   822846.0  
1          NaN          NaN        NaN  
2          NaN          NaN   273232.0  
3        222.0       7707.0   101060.0  
4          NaN          NaN   145773.0

## <font color=blue>2) Release information</font>

### Data from Musicbrainz.org

The objective of this project is to visualize when each artist released for the first time a certain CD/Album/Single etc.

If we look at the "releases" table:

In [70]:
releases = pd.read_csv('Musicbrainz/Tables_used/release.txt',sep='\t', header=None, engine='c', usecols=[0,2,3,4])
releases.columns = ['release_id','release_group','credit_id','group_id']
releases.head()

release_id           release_group  credit_id  group_id
0           9       A Sorta Fairytale         60    896742
1          10       A Sorta Fairytale         60    896742
2          11       Glory of the 80's         60     95360
3          12  Silent All These Years         60    104189
4          26                  Demons      20211     94299

We can see, in the first 2 rows, that the same CD/Album can be released/remastered many times. According to Musicbrainz's field description for each release (https://musicbrainz.org/doc/Release):

"A MusicBrainz release represents the unique release (i.e. issuing) of a product on a specific date with specific release information such as the country, label, barcode and packaging. If you walk into a store and purchase an album or single, they are each represented in MusicBrainz as one release".

If we look at another release-related field in Musicbrainz, we find the "release group" (https://musicbrainz.org/doc/Release_Group):

"A release group, just as the name suggests, is used to group several different releases into a single logical entity. Every release belongs to one, and only one release group.

Both release groups and releases are "albums" in a general sense, but with an important difference: a release is something you can buy as media such as a CD or a vinyl record, while a release group embraces the overall concept of an album -- it doesn't matter how many CDs or editions/versions it had."

By reading these descriptions, we can clearly see that the release group is the table we are looking for as it represents a single creation, no matter how many times it has been edited or released afterwards. So we will have to keep the first release id for each release group.

In [71]:
release_country = pd.read_csv('Musicbrainz/Tables_used/release_country.txt',sep='\t', header=None, engine='c', usecols=[0,1,2])
release_country.columns = ['release_id','area_id','release_year']
release_country.head()

release_id  area_id  release_year
0           3       81        1997.0
1     1427792      107        2014.0
2           9       81        2002.0
3          10      221        2002.0
4          11       81        1999.0

In [72]:
df2 = pd.merge(releases, release_country, how='left', on='release_id')
df2.head()

release_id           release_group  credit_id  group_id  area_id  \
0           9       A Sorta Fairytale         60    896742     81.0   
1          10       A Sorta Fairytale         60    896742    221.0   
2          11       Glory of the 80's         60     95360     81.0   
3          12  Silent All These Years         60    104189     81.0   
4          26                  Demons      20211     94299    107.0   

   release_year  
0        2002.0  
1        2002.0  
2        1999.0  
3        1997.0  
4        1998.0

In [73]:
#Let's see how many releases we have:
df2['release_id'].nunique()

2198457

In [74]:
df2.isnull().sum(axis=0)

release_id            0
release_group         7
credit_id             0
group_id              0
area_id          287376
release_year     341983
dtype: int64

In [75]:
#We want to keep only the releases which have a release year, so we can drop the others:
df2.dropna(subset=['release_year'], axis=0, inplace=True)
df2['release_year'] = df2.release_year.astype(int,inplace=True)
df2['release_id'].nunique()

1859982

In [76]:
#Let's analyze the year column:
pd.options.display.max_rows = 2000
df2.groupby('release_year').count()

release_id  release_group  credit_id  group_id  area_id
release_year                                                         
1                      2              2          2         2        2
4                      1              1          1         1        1
5                      5              5          5         5        5
7                      1              1          1         1        1
8                      2              2          2         2        2
10                     3              3          3         3        3
14                     1              1          1         1        1
17                     4              4          4         4        4
18                     1              1          1         1        1
19                     3              3          3         3        3
20                     2              2          2         2        2
21                     1              1          1         1        1
23                     1              1          1         1        1
24                     1              1          1         1        1
25                     2              2          2         2        2
28                     2              2          2         2        2
29                     2              2          2         2        2
31                     2              2          2         2        2
73                     1              1          1         1        1
195                    1              1          1         1        1
198                    1              1          1         1        1
199                    2              2          2         2        2
200                    4              4          4         4        4
201                    4              4          4         4        4
209                    2              2          2         2        2
666                    1              1          1         1        1
701                    1              1          1         1        1
996                    1              1          1         1        1
1009                   1              1          1         1        1
1029                   1              1          1         1        1
1198                   1              1          1         1        1
1694                   1              1          1         1        1
1886                   1              1          1         1        1
1889                   1              1          1         1        1
1890                 249            249        249       249      249
1891                  11             11         11        11       11
1892                 130            130        130       130      130
1893                 183            183        183       183      183
1894                  29             29         29        29       29
1895                   2              2          2         2        2
1896                   6              6          6         6        6
1897                  65             65         65        65       65
1898                 183            183        183       183      183
1899                 281            281        281       281      281
1900                 131            131        131       131      131
1901                 199            199        199       199      199
1902                 234            234        234       234      234
1903                 196            196        196       196      196
1904                 155            155        155       155      155
1905                 163            163        163       163      163
1906                 154            154        154       154      154
1907                 171            171        171       171      171
1908                 212            212        212       212      212
1909                 187            187        187       187      187
1910                 115            115        115       115      115
1911                  54

By looking at the different year values, and, in order to have enough values per year, we could drop the rows whose year is below 1890 and above 2019. Our visualization would have 130 years, which is pretty good.

In [77]:
df2.drop(df2[df2['release_year'] < 1890].index , inplace=True)
df2.drop(df2[df2['release_year'] >2019].index , inplace=True)
df2.sort_values(by=['release_year']).head()

release_id                  release_group  credit_id  group_id  \
1266766      386919      Visions of Paradise Waltz      97546    712605   
1266956      386830  German Ballad with Variations      97546    712514   
1266958      386829  German Ballad with Variations      97546    712514   
1266960      386828           Mountain Bells Polka      97546    712513   
1266961      386827           Mountain Bells Polka      97546    712513   

         area_id  release_year  
1266766    222.0          1890  
1266956    222.0          1890  
1266958    222.0          1890  
1266960    222.0          1890  
1266961    222.0          1890

In [78]:
#Converting the year column to datetime for later:
df2['release_year'] = pd.to_datetime(df2['release_year'].astype(str), format='%Y')
df2.dtypes

release_id                int64
release_group            object
credit_id                 int64
group_id                  int64
area_id                 float64
release_year     datetime64[ns]
dtype: object

In [79]:
#We sort by release id and year (we could have 2 release groups with the same name but produced by different artists):
df2.sort_values(['release_group','release_year','credit_id'], ascending=[True,True,True], inplace=True)
df2.head()

release_id            release_group  credit_id  group_id  area_id  \
2026273     2163750                             2205562   1962329    240.0   
1648516     1846605                             1503027   1713833    240.0   
1250325     1714060    Beaux Soirs De Paris     1324142   1609358     73.0   
2116340     2265346                    Le 1     2291833   2042812    240.0   
1748061     1895266   M2Music HitDisc Vol. 1          1   1751021    222.0   

        release_year  
2026273   2014-01-01  
1648516   2015-01-01  
1250325   1995-01-01  
2116340   2018-01-01  
1748061   2006-01-01

In [80]:
df2[df2['release_group'] == 'Artaxerxes']

release_id release_group  credit_id  group_id  area_id release_year
1836724     2378622    Artaxerxes    2392005   2132682    240.0   1996-01-01
1910376     2379252    Artaxerxes    2392005   2132682    221.0   2009-01-01
1909444     2379244    Artaxerxes    2392011   2133192    222.0   2011-01-01

In [81]:
#Now we can delete the duplicate releases and keep the ones who were first released:
df2.drop_duplicates(subset=['release_group','credit_id'],keep='first', inplace=True)
df2['release_id'].nunique()

1499614

In [82]:
#Just to double-check:
df2[df2['release_group'] == 'Artaxerxes']

release_id release_group  credit_id  group_id  area_id release_year
1836724     2378622    Artaxerxes    2392005   2132682    240.0   1996-01-01
1909444     2379244    Artaxerxes    2392011   2133192    222.0   2011-01-01

## <font color=blue>3) Matching releases with artists</font>

Now that we have both artist and releases dataframes, we can join them:

In [85]:
df3 = pd.merge(df2, df, how='left', on='credit_id')
df3.head()

release_id            release_group  credit_id  group_id  area_id  \
0     2163750                             2205562   1962329    240.0   
1     1846605                             1503027   1713833    240.0   
2     1714060    Beaux Soirs De Paris     1324142   1609358     73.0   
3     2265346                    Le 1     2291833   2042812    240.0   
4     1895266   M2Music HitDisc Vol. 1          1   1751021    222.0   

  release_year  artist_id                           artist_mbid  \
0   2014-01-01  1654312.0  d10d6441-dcc1-4202-93bf-0c0acf72913a   
1   2015-01-01  1112115.0  7b52c77b-1a34-439d-a285-3a7c69cb5b1a   
2   1995-01-01  1122795.0  71b8451c-c10a-400e-9544-101f34ab2522   
3   2018-01-01  1720981.0  a69efb5f-0b28-4328-8ff0-44d8d6f39755   
4   2006-01-01        1.0  89ad4ac3-39f7-470e-963a-56509c546377   

     artist_name_x  start_area1  start_area2  
0         Soul Glo       7707.0          NaN  
1      Ben Bennett          NaN          NaN  
2  Soixante Étages          NaN          NaN  
3         TedeuzeM      68613.0          NaN  
4  Various Artists          NaN          NaN

In [25]:
df3.isnull().sum(axis=0)

release_id            0
release_group         4
credit_id             0
group_id              0
area_id               0
release_year          0
artist_id           151
artist_mbid         151
artist_name_x       155
start_area1      430452
start_area2      959581
dtype: int64

In [26]:
df3['release_id'].nunique()

1499614

In [27]:
len(df3)

1724524

In [28]:
df3[df3['release_group']=='Artaxerxes']

release_id release_group  credit_id  group_id  area_id release_year  \
119493     2378622    Artaxerxes    2392005   2132682    240.0   1996-01-01   
119494     2378622    Artaxerxes    2392005   2132682    240.0   1996-01-01   
119495     2378622    Artaxerxes    2392005   2132682    240.0   1996-01-01   
119496     2378622    Artaxerxes    2392005   2132682    240.0   1996-01-01   
119497     2378622    Artaxerxes    2392005   2132682    240.0   1996-01-01   
119498     2378622    Artaxerxes    2392005   2132682    240.0   1996-01-01   
119499     2378622    Artaxerxes    2392005   2132682    240.0   1996-01-01   
119500     2378622    Artaxerxes    2392005   2132682    240.0   1996-01-01   
119501     2378622    Artaxerxes    2392005   2132682    240.0   1996-01-01   
119502     2379244    Artaxerxes    2392011   2133192    222.0   2011-01-01   
119503     2379244    Artaxerxes    2392011   2133192    222.0   2011-01-01   
119504     2379244    Artaxerxes    2392011   2133192    222.0   2011-01-01   

        artist_id                           artist_mbid  \
119493   391603.0  e3062782-ab7b-41bc-8e65-aeea16dc1a89   
119494   124232.0  4e7f1926-8704-4545-a1a1-ded91651c884   
119495   688791.0  f34e9da4-2ee7-4f27-aa34-adc5db791bec   
119496  1129787.0  c33f733e-2bf4-402b-9455-1a293601a1cd   
119497  1104538.0  5680c729-615b-47e2-969e-27a087c572fb   
119498   402986.0  70af5d9a-c6e0-4fcf-9cde-4d3d00e0fcb0   
119499   183632.0  954d1c83-259f-4a25-8878-10c19bb097af   
119500    87510.0  857588a5-b7aa-4f72-a87b-8f03dca60e30   
119501  1078968.0  93da7aaa-250b-46e1-b5ef-0ad78d46dc3f   
119502   854064.0  a87f2b39-84c7-4888-935c-d41943bd7971   
119503   124232.0  4e7f1926-8704-4545-a1a1-ded91651c884   
119504   989288.0  4c05f6e6-7a40-437e-9f12-a90c1da7b4f8   

                    artist_name_x  start_area1  start_area2  
119493              Ian Partridge        221.0       1178.0  
119494                Thomas Arne        221.0       1178.0  
119495         Christopher Robson          NaN          NaN  
119496            Patricia Spence          NaN          NaN  
119497              Philippa Hyde        221.0          NaN  
119498  The Parley of Instruments        221.0       1178.0  
119499             Catherine Bott        221.0          NaN  
119500                Roy Goodman        221.0      30926.0  
119501       Richard Edgar‐Wilson          NaN          NaN  
119502    Classical Opera Company        221.0          NaN  
119503                Thomas Arne        221.0       1178.0  
119504                   Ian Page        221.0          NaN

If we look at the above, we can see that there is one line per each artist that participated for each release ID.

As we don't want to show duplicate releases, we need to keep only one artist per release. We will keep the first artist appearing for each release (even though we know this is not 100% accurate, but we have to avoid duplicates). This will afftect 224.910 rows under a total of 1.499.614 unique releases, so 14% of our dataset.

In [29]:
#Now we can delete the duplicate releases and keep the ones who were first released:
df3.drop_duplicates(subset=['release_id'],keep='first', inplace=True)
df3['release_id'].nunique()

1499614

In [30]:
len(df3)

1499614

## <font color=blue>4) Geographical data</font>

### Data from Musicbrainz.org

The idea of the visualization is to see where each gender comes from, so, ideally, we would have to look at the artists origins (start area: last 2 columns of our dataframe).

In our dataframe df3, the 5th column "area_id" is related to the area where the release was produced. This isn't directly related to the origin of an artist/band, as many artists have to record their works in different countries/or areas.

Let's see for how many releases we have that information:

In [31]:
df3.isnull().sum(axis=0)

release_id            0
release_group         4
credit_id             0
group_id              0
area_id               0
release_year          0
artist_id           151
artist_mbid         151
artist_name_x       155
start_area1      404503
start_area2      876562
dtype: int64

In Musicbrainz's database, we have some tables related to the areas. Let's see how we can use them to input more geographical information into our dataframe:

In [14]:
areas = pd.read_csv('Musicbrainz/Tables_used/area.txt',sep='\t', header=None, engine='python', usecols=[0,2,3])
areas.columns = ['area_id','area_name','code_type']
areas.head()

area_id area_name  code_type
0    15449   Greccio        4.0
1       38    Canada        1.0
2       43     Chile        1.0
3       44     China        1.0
4       36  Cambodia        1.0

In [15]:
#Let's see the area types we have:
area_types = pd.read_csv('Musicbrainz/Tables_used/area_type.txt',sep='\t', header=None, engine='python', usecols=[1,3,4], error_bad_lines=False)
area_types.columns = ['type','code_type','definition']
area_types.head(20)

type  code_type                                         definition
0       Country          1  Country is used for areas included (or previou...
1   Subdivision          2  Subdivision is used for the main administrativ...
2        County          7  County is used for smaller administrative divi...
3  Municipality          4  Municipality is used for small administrative ...
4          City          3  City is used for settlements of any size, incl...
5      District          5  District is used for a division of a large cit...
6        Island          6  Island is used for islands and atolls which do...

ISO tables: In order to retrieve the ISO code for the countries and states, Musicbrainz provides us with 2 tables which contain: area_id and their ISO code (for area code_types 1 and 2: country and subdivision). These are international standard codes set by the International organization for Standardization (www.iso.org).

We will add this information to our areas dataframe, as this will be usefull for our visualization.

In [16]:
#First, we load the first ISO file:
ISO1 = pd.read_csv('Musicbrainz/Tables_used/iso_3166_1.txt',sep='\t', header=None, engine='python')
ISO1.columns = ['area_id','ISO_code']

Note: as the only countries for which we would like to retrieve the subdivision are large countries (USA, Canada and Australia) for our visualization to work, we can at this early stage remove from ISO2 the rows not related to those countries:

In [17]:
#Loading ISO2 file:
ISO2 = pd.read_csv('Musicbrainz/Tables_used/iso_3166_2.txt',sep=',', header=None, engine='python')
ISO2.columns = ['area_id','ISO_code', 'ISO_country']
ISO2_target = pd.concat([ISO2[ISO2['ISO_country'] == 'CA'],ISO2[ISO2['ISO_country'] == 'US'],ISO2[ISO2['ISO_country'] == 'AU']])
ISO2_target.head()

area_id ISO_code ISO_country
602      312    CA-AB          CA
603      313    CA-BC          CA
604      314    CA-MB          CA
605      315    CA-NB          CA
606      316    CA-NL          CA

In [18]:
#We drop the column ISO_country to concatenate:
ISO2_target.drop(labels='ISO_country', axis=1, inplace=True)

In [19]:
#Now, we can add both ISO dataframes together:
ISO_codes = pd.concat([ISO1, ISO2_target])
ISO_codes.head()

area_id ISO_code
0        1       AF
1        2       AL
2        3       DZ
3        4       AS
4        5       AD

In [20]:
#And finally, we can merge the ISO codes into the areas dataframe:
areas_ISO = pd.merge(areas, ISO_codes, how='left', on='area_id')
areas_ISO.head()

area_id area_name  code_type ISO_code
0    15449   Greccio        4.0      NaN
1       38    Canada        1.0       CA
2       43     Chile        1.0       CL
3       44     China        1.0       CN
4       36  Cambodia        1.0       KH

In [39]:
#Add the areas information to our main dataframe for the column "area_id":
df4 = pd.merge(df3, areas_ISO, how='left', on='area_id')
df4.head()

release_id            release_group  credit_id  group_id  area_id  \
0     2163750                             2205562   1962329    240.0   
1     1846605                             1503027   1713833    240.0   
2     1714060    Beaux Soirs De Paris     1324142   1609358     73.0   
3     2265346                    Le 1     2291833   2042812    240.0   
4     1895266   M2Music HitDisc Vol. 1          1   1751021    222.0   

  release_year  artist_id                           artist_mbid  \
0   2014-01-01  1654312.0  d10d6441-dcc1-4202-93bf-0c0acf72913a   
1   2015-01-01  1112115.0  7b52c77b-1a34-439d-a285-3a7c69cb5b1a   
2   1995-01-01  1122795.0  71b8451c-c10a-400e-9544-101f34ab2522   
3   2018-01-01  1720981.0  a69efb5f-0b28-4328-8ff0-44d8d6f39755   
4   2006-01-01        1.0  89ad4ac3-39f7-470e-963a-56509c546377   

     artist_name_x  start_area1  start_area2      area_name  code_type  \
0         Soul Glo       7707.0          NaN    [Worldwide]        NaN   
1      Ben Bennett          NaN          NaN    [Worldwide]        NaN   
2  Soixante Étages          NaN          NaN         France        1.0   
3         TedeuzeM      68613.0          NaN    [Worldwide]        NaN   
4  Various Artists          NaN          NaN  United States        1.0   

  ISO_code  
0       XW  
1       XW  
2       FR  
3       XW  
4       US

In [40]:
#Rearranging dataframe columns to have a clearer dataframe and do the next merging:
df4 = df4[['release_id','group_id','release_group','credit_id','area_id','area_name','ISO_code','code_type','release_year','artist_id','artist_mbid','artist_name_x','start_area1','start_area2']]
df4.rename(columns={'area_id':'release_area','area_name':'release_area_name','code_type':'release_code_type','ISO_code':'release_ISO_code','start_area1':'area_id'}, inplace=True)
df4.head()

release_id  group_id            release_group  credit_id  release_area  \
0     2163750   1962329                             2205562         240.0   
1     1846605   1713833                             1503027         240.0   
2     1714060   1609358    Beaux Soirs De Paris     1324142          73.0   
3     2265346   2042812                    Le 1     2291833         240.0   
4     1895266   1751021   M2Music HitDisc Vol. 1          1         222.0   

  release_area_name release_ISO_code  release_code_type release_year  \
0       [Worldwide]               XW                NaN   2014-01-01   
1       [Worldwide]               XW                NaN   2015-01-01   
2            France               FR                1.0   1995-01-01   
3       [Worldwide]               XW                NaN   2018-01-01   
4     United States               US                1.0   2006-01-01   

   artist_id                           artist_mbid    artist_name_x  area_id  \
0  1654312.0  d10d6441-dcc1-4202-93bf-0c0acf72913a         Soul Glo   7707.0   
1  1112115.0  7b52c77b-1a34-439d-a285-3a7c69cb5b1a      Ben Bennett      NaN   
2  1122795.0  71b8451c-c10a-400e-9544-101f34ab2522  Soixante Étages      NaN   
3  1720981.0  a69efb5f-0b28-4328-8ff0-44d8d6f39755         TedeuzeM  68613.0   
4        1.0  89ad4ac3-39f7-470e-963a-56509c546377  Various Artists      NaN   

   start_area2  
0          NaN  
1          NaN  
2          NaN  
3          NaN  
4          NaN

In [41]:
#Add the start area name and type to our main dataframe for the column "area id"(which was "start area 1" before):
df5 = pd.merge(df4, areas_ISO, how='left', on='area_id')
df5.head()

release_id  group_id            release_group  credit_id  release_area  \
0     2163750   1962329                             2205562         240.0   
1     1846605   1713833                             1503027         240.0   
2     1714060   1609358    Beaux Soirs De Paris     1324142          73.0   
3     2265346   2042812                    Le 1     2291833         240.0   
4     1895266   1751021   M2Music HitDisc Vol. 1          1         222.0   

  release_area_name release_ISO_code  release_code_type release_year  \
0       [Worldwide]               XW                NaN   2014-01-01   
1       [Worldwide]               XW                NaN   2015-01-01   
2            France               FR                1.0   1995-01-01   
3       [Worldwide]               XW                NaN   2018-01-01   
4     United States               US                1.0   2006-01-01   

   artist_id                           artist_mbid    artist_name_x  area_id  \
0  1654312.0  d10d6441-dcc1-4202-93bf-0c0acf72913a         Soul Glo   7707.0   
1  1112115.0  7b52c77b-1a34-439d-a285-3a7c69cb5b1a      Ben Bennett      NaN   
2  1122795.0  71b8451c-c10a-400e-9544-101f34ab2522  Soixante Étages      NaN   
3  1720981.0  a69efb5f-0b28-4328-8ff0-44d8d6f39755         TedeuzeM  68613.0   
4        1.0  89ad4ac3-39f7-470e-963a-56509c546377  Various Artists      NaN   

   start_area2        area_name  code_type ISO_code  
0          NaN     Philadelphia        3.0      NaN  
1          NaN              NaN        NaN      NaN  
2          NaN              NaN        NaN      NaN  
3          NaN  Aix-en-Provence        3.0      NaN  
4          NaN              NaN        NaN      NaN

In [42]:
#Rearranging dataframe columns to have a clearer dataframe:
df5 = df5[['release_id','group_id','release_group','credit_id','release_area','release_area_name','release_ISO_code','release_code_type','release_year','artist_id','artist_mbid','artist_name_x','area_id','area_name','ISO_code','code_type','start_area2']]
df5.rename(columns={'area_id':'artist_area1','area_name':'artist_area_name1','ISO_code':'artist_ISO_code1','code_type':'artist_code_type1','start_area2':'area_id'}, inplace=True)
df5.head()

release_id  group_id            release_group  credit_id  release_area  \
0     2163750   1962329                             2205562         240.0   
1     1846605   1713833                             1503027         240.0   
2     1714060   1609358    Beaux Soirs De Paris     1324142          73.0   
3     2265346   2042812                    Le 1     2291833         240.0   
4     1895266   1751021   M2Music HitDisc Vol. 1          1         222.0   

  release_area_name release_ISO_code  release_code_type release_year  \
0       [Worldwide]               XW                NaN   2014-01-01   
1       [Worldwide]               XW                NaN   2015-01-01   
2            France               FR                1.0   1995-01-01   
3       [Worldwide]               XW                NaN   2018-01-01   
4     United States               US                1.0   2006-01-01   

   artist_id                           artist_mbid    artist_name_x  \
0  1654312.0  d10d6441-dcc1-4202-93bf-0c0acf72913a         Soul Glo   
1  1112115.0  7b52c77b-1a34-439d-a285-3a7c69cb5b1a      Ben Bennett   
2  1122795.0  71b8451c-c10a-400e-9544-101f34ab2522  Soixante Étages   
3  1720981.0  a69efb5f-0b28-4328-8ff0-44d8d6f39755         TedeuzeM   
4        1.0  89ad4ac3-39f7-470e-963a-56509c546377  Various Artists   

   artist_area1 artist_area_name1 artist_ISO_code1  artist_code_type1  area_id  
0        7707.0      Philadelphia              NaN                3.0      NaN  
1           NaN               NaN              NaN                NaN      NaN  
2           NaN               NaN              NaN                NaN      NaN  
3       68613.0   Aix-en-Provence              NaN                3.0      NaN  
4           NaN               NaN              NaN                NaN      NaN

In [43]:
#Add the start area 2 name and type to our main dataframe for the column "area id"(which was "start area 2" before):
df6 = pd.merge(df5, areas_ISO, how='left', on='area_id')
df6.head()

release_id  group_id            release_group  credit_id  release_area  \
0     2163750   1962329                             2205562         240.0   
1     1846605   1713833                             1503027         240.0   
2     1714060   1609358    Beaux Soirs De Paris     1324142          73.0   
3     2265346   2042812                    Le 1     2291833         240.0   
4     1895266   1751021   M2Music HitDisc Vol. 1          1         222.0   

  release_area_name release_ISO_code  release_code_type release_year  \
0       [Worldwide]               XW                NaN   2014-01-01   
1       [Worldwide]               XW                NaN   2015-01-01   
2            France               FR                1.0   1995-01-01   
3       [Worldwide]               XW                NaN   2018-01-01   
4     United States               US                1.0   2006-01-01   

   artist_id                           artist_mbid    artist_name_x  \
0  1654312.0  d10d6441-dcc1-4202-93bf-0c0acf72913a         Soul Glo   
1  1112115.0  7b52c77b-1a34-439d-a285-3a7c69cb5b1a      Ben Bennett   
2  1122795.0  71b8451c-c10a-400e-9544-101f34ab2522  Soixante Étages   
3  1720981.0  a69efb5f-0b28-4328-8ff0-44d8d6f39755         TedeuzeM   
4        1.0  89ad4ac3-39f7-470e-963a-56509c546377  Various Artists   

   artist_area1 artist_area_name1 artist_ISO_code1  artist_code_type1  \
0        7707.0      Philadelphia              NaN                3.0   
1           NaN               NaN              NaN                NaN   
2           NaN               NaN              NaN                NaN   
3       68613.0   Aix-en-Provence              NaN                3.0   
4           NaN               NaN              NaN                NaN   

   area_id area_name  code_type ISO_code  
0      NaN       NaN        NaN      NaN  
1      NaN       NaN        NaN      NaN  
2      NaN       NaN        NaN      NaN  
3      NaN       NaN        NaN      NaN  
4      NaN       NaN        NaN      NaN

In [44]:
#Renaming columns:
df6.rename(columns={'area_id':'artist_area2','area_name':'artist_area_name2','code_type':'artist_code_type2', 'ISO_code':'artist_ISO_code2'}, inplace=True)
df6.head()

release_id  group_id            release_group  credit_id  release_area  \
0     2163750   1962329                             2205562         240.0   
1     1846605   1713833                             1503027         240.0   
2     1714060   1609358    Beaux Soirs De Paris     1324142          73.0   
3     2265346   2042812                    Le 1     2291833         240.0   
4     1895266   1751021   M2Music HitDisc Vol. 1          1         222.0   

  release_area_name release_ISO_code  release_code_type release_year  \
0       [Worldwide]               XW                NaN   2014-01-01   
1       [Worldwide]               XW                NaN   2015-01-01   
2            France               FR                1.0   1995-01-01   
3       [Worldwide]               XW                NaN   2018-01-01   
4     United States               US                1.0   2006-01-01   

   artist_id                           artist_mbid    artist_name_x  \
0  1654312.0  d10d6441-dcc1-4202-93bf-0c0acf72913a         Soul Glo   
1  1112115.0  7b52c77b-1a34-439d-a285-3a7c69cb5b1a      Ben Bennett   
2  1122795.0  71b8451c-c10a-400e-9544-101f34ab2522  Soixante Étages   
3  1720981.0  a69efb5f-0b28-4328-8ff0-44d8d6f39755         TedeuzeM   
4        1.0  89ad4ac3-39f7-470e-963a-56509c546377  Various Artists   

   artist_area1 artist_area_name1 artist_ISO_code1  artist_code_type1  \
0        7707.0      Philadelphia              NaN                3.0   
1           NaN               NaN              NaN                NaN   
2           NaN               NaN              NaN                NaN   
3       68613.0   Aix-en-Provence              NaN                3.0   
4           NaN               NaN              NaN                NaN   

   artist_area2 artist_area_name2  artist_code_type2 artist_ISO_code2  
0           NaN               NaN                NaN              NaN  
1           NaN               NaN                NaN              NaN  
2           NaN               NaN                NaN              NaN  
3           NaN               NaN                NaN              NaN  
4           NaN               NaN                NaN              NaN

Now that we have the names of the different areas, let's check what kind of information we have in those columns.

As we said before, we prefer to keep the artist area preferably, as it represents more the real origin of the music.

1) Artist area 1:

In [45]:
df6.artist_area_name1.value_counts()

United States                                                 273545
United Kingdom                                                133070
Japan                                                          83908
Germany                                                        67463
France                                                         45927
Italy                                                          27215
Sweden                                                         24983
Canada                                                         23619
Finland                                                        21981
Netherlands                                                    18101
Australia                                                      17738
Spain                                                          16090
Russia                                                         13821
Brazil                                                         11142
Belgium                           

In [46]:
df6.artist_code_type1.value_counts()

1.0    954997
3.0    112299
2.0     24835
4.0      3058
5.0      2431
7.0       254
6.0       114
Name: artist_code_type1, dtype: int64

As we can see, the majority of the artists' start area type we have is related to countries. This would be good for our visualization except for big countries like USA, Canada or Australia, for which we would prefer to retrieve at least the artist's state/subdivision, to have a clearer view of the music's origin.

Also, we noticed that we have some area names that don't give us much information: "Worldwide", "Europe", "South Australia", etc.

2) Artist area 2:

In [47]:
df6.artist_area_name2.value_counts()

London                                         23087
Los Angeles                                    14173
New York                                       12554
Chicago                                         8353
Tokyo                                           7784
Paris                                           6395
Brooklyn                                        6307
Berlin                                          5941
Philadelphia                                    5276
Detroit                                         4659
San Francisco                                   4574
Toronto                                         4068
Boston                                          4036
Seattle                                         3938
Seoul                                           3800
Stockholm                                       3449
Melbourne                                       3308
Hamburg                                         3259
United Kingdom                                

In [48]:
df6.artist_code_type2.value_counts()

3.0    482663
2.0     61579
1.0     32265
5.0     25649
4.0     20562
7.0      2490
6.0       557
Name: artist_code_type2, dtype: int64

It looks like this second column could be giving us more detailed information about the artist's origin (only 31K rows have countries).

### Data from simplemaps.com

There is a free downloadable file in https://simplemaps.com/data/world-cities, which provides us with the names of the major cities in the world, as well as their country, subdivision and ISO code (for the country).

I have downloaded the csv version and we'll use it to classify our areas columns.

In [10]:
cities = pd.read_csv('worldcities.csv', sep=',', usecols=[1,4,5], encoding='utf-8')
cities.columns = ['area_name','country','country_ISO']
cities.head()

area_name country country_ISO
0    Malisheve  Kosovo          XK
1      Prizren  Kosovo          XK
2  Zubin Potok  Kosovo          XK
3     Kamenice  Kosovo          XK
4         Viti  Kosovo          XK

Note: as we will merge the above dataframe later with our main dataframe using the "area_name" as key, we need to make sure that we remove the areas which have the same name, as we don't want to input the wrong information:

In [11]:
cities.drop_duplicates(subset='area_name', keep=False, inplace=True)

What we will do next is: 

1) For the rows whose artist_area_name1 is a country, we save it as the release origin. For the rows who have a subdivision, we keep only the ones related to USA, Canada or Australia (ie: the only ones who have area code =2 and ISO code not null, as we decided earlier when we generated the ISO2_target dataframe).

2) For the rows which don't have country or subdivision, we will match the artist_area_name1 with its country using the cities dataframe.


3) For the rows we don't have information with artist_area_name1, we will look into artist_area_name2 and repeat steps 1 & 2.

#### 1) Keeping the origin for rows who have already a country or subdivision in artist_area1:

In [51]:
# Adding the origin columns for the rows who have a subdivision (ie: USA, Canada and Australia):
df6['origin_code'] = np.nan
df6['origin_name'] = np.nan
df6['origin_ISO_code'] = np.nan
df6['origin_code_type'] = np.nan
df6.origin_code = np.where(np.logical_and(df6.artist_code_type1.isin([2]),df6.artist_ISO_code1.notnull()) , df6.artist_area1, df6.origin_code)
df6.origin_name = np.where(np.logical_and(df6.artist_code_type1.isin([2]),df6.artist_ISO_code1.notnull()) , df6.artist_area_name1, df6.origin_name)
df6.origin_ISO_code = np.where(np.logical_and(df6.artist_code_type1.isin([2]),df6.artist_ISO_code1.notnull()) , df6.artist_ISO_code1, df6.origin_ISO_code)
df6.origin_code_type = np.where(np.logical_and(df6.artist_code_type1.isin([2]),df6.artist_ISO_code1.notnull()) , df6.artist_code_type1, df6.origin_code_type)
df6.head()

release_id  group_id            release_group  credit_id  release_area  \
0     2163750   1962329                             2205562         240.0   
1     1846605   1713833                             1503027         240.0   
2     1714060   1609358    Beaux Soirs De Paris     1324142          73.0   
3     2265346   2042812                    Le 1     2291833         240.0   
4     1895266   1751021   M2Music HitDisc Vol. 1          1         222.0   

  release_area_name release_ISO_code  release_code_type release_year  \
0       [Worldwide]               XW                NaN   2014-01-01   
1       [Worldwide]               XW                NaN   2015-01-01   
2            France               FR                1.0   1995-01-01   
3       [Worldwide]               XW                NaN   2018-01-01   
4     United States               US                1.0   2006-01-01   

   artist_id  ... artist_ISO_code1 artist_code_type1  artist_area2  \
0  1654312.0  ...              NaN               3.0           NaN   
1  1112115.0  ...              NaN               NaN           NaN   
2  1122795.0  ...              NaN               NaN           NaN   
3  1720981.0  ...              NaN               3.0           NaN   
4        1.0  ...              NaN               NaN           NaN   

  artist_area_name2 artist_code_type2  artist_ISO_code2  origin_code  \
0               NaN               NaN               NaN          NaN   
1               NaN               NaN               NaN          NaN   
2               NaN               NaN               NaN          NaN   
3               NaN               NaN               NaN          NaN   
4               NaN               NaN               NaN          NaN   

  origin_name  origin_ISO_code origin_code_type  
0         NaN              NaN              NaN  
1         NaN              NaN              NaN  
2         NaN              NaN              NaN  
3         NaN              NaN              NaN  
4         NaN              NaN              NaN  

[5 rows x 24 columns]

In [52]:
#Now we add the information related to the country:
df6.origin_code = np.where(df6.artist_code_type1.isin([1]), df6.artist_area1, df6.origin_code)
df6.origin_name = np.where(df6.artist_code_type1.isin([1]), df6.artist_area_name1, df6.origin_name)
df6.origin_ISO_code = np.where(df6.artist_code_type1.isin([1]), df6.artist_ISO_code1, df6.origin_ISO_code)
df6.origin_code_type = np.where(df6.artist_code_type1.isin([1]), df6.artist_code_type1, df6.origin_code_type)

#### 2) Matching cities in artist_area_name1 with cities dataframe:

As we mentioned earlier, the merging between our main dataframe and the cities is going to be done by area_name. 

There are many cities in the world with the same name and we need to make sure that we don't take them into consideration, to avoid mismatching data.

We will analyze separately the artist_area_name1 items and match them with the cities dataframe (only for the not duplicated city names).

In [53]:
cities_to_match = df6[df6['artist_code_type1'] == 3]
cities_to_match.head()

release_id  group_id           release_group  credit_id  release_area  \
0      2163750   1962329                            2205562         240.0   
3      2265346   2042812                   Le 1     2291833         240.0   
5      1772538   1656147            devil jokes     1653884         240.0   
22      890832    426451  !!! En boka zerrada...     300620         194.0   
54     2232738   2017354                  !NADA!    1629941         240.0   

   release_area_name release_ISO_code  release_code_type release_year  \
0        [Worldwide]               XW                NaN   2014-01-01   
3        [Worldwide]               XW                NaN   2018-01-01   
5        [Worldwide]               XW                NaN   2016-01-01   
22             Spain               ES                1.0   2001-01-01   
54       [Worldwide]               XW                NaN   2015-01-01   

    artist_id  ... artist_ISO_code1 artist_code_type1  artist_area2  \
0   1654312.0  ...              NaN               3.0           NaN   
3   1720981.0  ...              NaN               3.0           NaN   
5   1363025.0  ...              NaN               3.0           NaN   
22   300620.0  ...              NaN               3.0           NaN   
54  1345721.0  ...              NaN               3.0           NaN   

   artist_area_name2 artist_code_type2  artist_ISO_code2  origin_code  \
0                NaN               NaN               NaN          NaN   
3                NaN               NaN               NaN          NaN   
5                NaN               NaN               NaN          NaN   
22               NaN               NaN               NaN          NaN   
54               NaN               NaN               NaN          NaN   

   origin_name  origin_ISO_code origin_code_type  
0          NaN              NaN              NaN  
3          NaN              NaN              NaN  
5          NaN              NaN              NaN  
22         NaN              NaN              NaN  
54         NaN              NaN              NaN  

[5 rows x 24 columns]

In [54]:
#We remove the duplicate city names:
cities_to_match.drop_duplicates(subset='artist_area_name1', keep=False, inplace=True)
#We remove the columns that we don't need:
columns = ['group_id', 'release_group', 'credit_id', 'release_area',
       'release_area_name', 'release_ISO_code', 'release_code_type',
       'release_year', 'artist_id', 'artist_mbid', 'artist_name_x',
       'artist_area1', 'artist_area2', 'artist_area_name2',
       'artist_code_type2', 'artist_ISO_code2', 'origin_code', 'origin_name',
       'origin_ISO_code', 'origin_code_type']
cities_to_match.drop(labels=columns, axis=1, inplace=True)

cities_to_match.head()

/home/ainhoa/anaconda3/envs/kschool/lib/python3.7/site-packages/ipykernel_launcher.py:2: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-copy
  
/home/ainhoa/anaconda3/envs/kschool/lib/python3.7/site-packages/pandas/core/frame.py:3940: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-copy
  errors=errors)


release_id artist_area_name1 artist_ISO_code1  artist_code_type1
618      1960646         Barbières              NaN                3.0
4981     2055697           Torreón              NaN                3.0
5346     1320982          Mariupol              NaN                3.0
5559     1891407          Eschwege              NaN                3.0
6995     2313686             Haedo              NaN                3.0

In [55]:
#And now we can do the merging with the cities dataframe:
cities_matched = pd.merge(cities_to_match, cities, how='left', left_on='artist_area_name1', right_on='area_name')
cities_matched.head(20)

release_id      artist_area_name1 artist_ISO_code1  artist_code_type1  \
0      1960646              Barbières              NaN                3.0   
1      2055697                Torreón              NaN                3.0   
2      1320982               Mariupol              NaN                3.0   
3      1891407               Eschwege              NaN                3.0   
4      2313686                  Haedo              NaN                3.0   
5      1711186                  Lutsk              NaN                3.0   
6      1584076                Tomball              NaN                3.0   
7      1447250            Platteville              NaN                3.0   
8      1709159              Pinneberg              NaN                3.0   
9      2318988        Piekary Śląskie              NaN                3.0   
10     1779523           Barquisimeto              NaN                3.0   
11     2343300                 Cosmos              NaN                3.0   
12     1881937             Marblehead              NaN                3.0   
13     1981260                Karviná              NaN                3.0   
14     1572365                 Suzhou              NaN                3.0   
15     2265611                Vaassen              NaN                3.0   
16     2261181  Royal Tunbridge Wells              NaN                3.0   
17      775763               Rockland              NaN                3.0   
18     1679619              Amstetten              NaN                3.0   
19     2361582                  Barry              NaN                3.0   

       area_name        country country_ISO  
0            NaN            NaN         NaN  
1            NaN            NaN         NaN  
2       Mariupol        Ukraine          UA  
3            NaN            NaN         NaN  
4            NaN            NaN         NaN  
5          Lutsk        Ukraine          UA  
6        Tomball  United States          US  
7    Platteville  United States          US  
8            NaN            NaN         NaN  
9            NaN            NaN         NaN  
10  Barquisimeto      Venezuela          VE  
11           NaN            NaN         NaN  
12           NaN            NaN         NaN  
13           NaN            NaN         NaN  
14           NaN            NaN         NaN  
15           NaN            NaN         NaN  
16           NaN            NaN         NaN  
17      Rockland  United States          US  
18           NaN            NaN         NaN  
19           NaN            NaN         NaN

In [56]:
#Now we can input this information into our main dataframe:
df7 = pd.merge(df6, cities_matched, how='left', on='release_id')
df7.head()

release_id  group_id            release_group  credit_id  release_area  \
0     2163750   1962329                             2205562         240.0   
1     1846605   1713833                             1503027         240.0   
2     1714060   1609358    Beaux Soirs De Paris     1324142          73.0   
3     2265346   2042812                    Le 1     2291833         240.0   
4     1895266   1751021   M2Music HitDisc Vol. 1          1         222.0   

  release_area_name release_ISO_code  release_code_type release_year  \
0       [Worldwide]               XW                NaN   2014-01-01   
1       [Worldwide]               XW                NaN   2015-01-01   
2            France               FR                1.0   1995-01-01   
3       [Worldwide]               XW                NaN   2018-01-01   
4     United States               US                1.0   2006-01-01   

   artist_id  ... origin_code origin_name  origin_ISO_code origin_code_type  \
0  1654312.0  ...         NaN         NaN              NaN              NaN   
1  1112115.0  ...         NaN         NaN              NaN              NaN   
2  1122795.0  ...         NaN         NaN              NaN              NaN   
3  1720981.0  ...         NaN         NaN              NaN              NaN   
4        1.0  ...         NaN         NaN              NaN              NaN   

  artist_area_name1_y  artist_ISO_code1_y  artist_code_type1_y area_name  \
0                 NaN                 NaN                  NaN       NaN   
1                 NaN                 NaN                  NaN       NaN   
2                 NaN                 NaN                  NaN       NaN   
3                 NaN                 NaN                  NaN       NaN   
4                 NaN                 NaN                  NaN       NaN   

   country country_ISO  
0      NaN         NaN  
1      NaN         NaN  
2      NaN         NaN  
3      NaN         NaN  
4      NaN         NaN  

[5 rows x 30 columns]

In [57]:
#We input the info in the last columns into our origin columns:
df7.origin_code = np.where(df7.country_ISO.notnull(), df7.artist_area1, df7.origin_code)
df7.origin_name = np.where(df7.country_ISO.notnull(), df7.artist_area_name1_x, df7.origin_name)
df7.origin_ISO_code = np.where(df7.country_ISO.notnull(), df7.country_ISO, df7.origin_ISO_code)
df7.origin_code_type = np.where(df7.country_ISO.notnull(), df7.artist_code_type1_x, df7.origin_ISO_code)

In [58]:
#And now we can delete all the columns related to artist area1 and the ones generated in the last step:
remove = ['artist_area1', 'artist_area_name1_x', 'artist_ISO_code1_x','artist_code_type1_x','artist_area_name1_y',
       'artist_ISO_code1_y', 'artist_code_type1_y', 'area_name', 'country',
       'country_ISO']
df7.drop(labels=remove, axis=1, inplace=True)
df7.head()

release_id  group_id            release_group  credit_id  release_area  \
0     2163750   1962329                             2205562         240.0   
1     1846605   1713833                             1503027         240.0   
2     1714060   1609358    Beaux Soirs De Paris     1324142          73.0   
3     2265346   2042812                    Le 1     2291833         240.0   
4     1895266   1751021   M2Music HitDisc Vol. 1          1         222.0   

  release_area_name release_ISO_code  release_code_type release_year  \
0       [Worldwide]               XW                NaN   2014-01-01   
1       [Worldwide]               XW                NaN   2015-01-01   
2            France               FR                1.0   1995-01-01   
3       [Worldwide]               XW                NaN   2018-01-01   
4     United States               US                1.0   2006-01-01   

   artist_id                           artist_mbid    artist_name_x  \
0  1654312.0  d10d6441-dcc1-4202-93bf-0c0acf72913a         Soul Glo   
1  1112115.0  7b52c77b-1a34-439d-a285-3a7c69cb5b1a      Ben Bennett   
2  1122795.0  71b8451c-c10a-400e-9544-101f34ab2522  Soixante Étages   
3  1720981.0  a69efb5f-0b28-4328-8ff0-44d8d6f39755         TedeuzeM   
4        1.0  89ad4ac3-39f7-470e-963a-56509c546377  Various Artists   

   artist_area2 artist_area_name2  artist_code_type2 artist_ISO_code2  \
0           NaN               NaN                NaN              NaN   
1           NaN               NaN                NaN              NaN   
2           NaN               NaN                NaN              NaN   
3           NaN               NaN                NaN              NaN   
4           NaN               NaN                NaN              NaN   

   origin_code origin_name origin_ISO_code origin_code_type  
0          NaN         NaN             NaN              NaN  
1          NaN         NaN             NaN              NaN  
2          NaN         NaN             NaN              NaN  
3          NaN         NaN             NaN              NaN  
4          NaN         NaN             NaN              NaN

In [59]:
#For how many releases do we have the origin ISO code so far?
df7.origin_ISO_code.isnull().value_counts()

False    965150
True     539852
Name: origin_ISO_code, dtype: int64

Not bad: we have 965.150 releases matched with their ISO code already (this means that we will be able to easily plot them with Tableau or any other visualization tool that supports ISO standards for geographical data).

We will follow now the last step: step 3

#### 3) For the rows we don't have information with artist_area_name1, we will look into artist_area_name2 and repeat steps 1 & 2.

In [60]:
#How much information do we have in the artist_code_type2 column?
df7.artist_code_type2.value_counts()

3.0    482663
2.0     61579
1.0     32265
5.0     25649
4.0     20562
7.0      2490
6.0       557
Name: artist_code_type2, dtype: int64

In [61]:
#We add the subdivision information from USA, Canada and Australia into the origin columns:
df7.origin_code = np.where(np.logical_and(df7.artist_code_type2.isin([2]),df7.artist_ISO_code2.notnull()) , df7.artist_area2, df7.origin_code)
df7.origin_name = np.where(np.logical_and(df7.artist_code_type2.isin([2]),df7.artist_ISO_code2.notnull()) , df7.artist_area_name2, df7.origin_name)
df7.origin_ISO_code = np.where(np.logical_and(df7.artist_code_type2.isin([2]),df7.artist_ISO_code2.notnull()) , df7.artist_ISO_code2, df7.origin_ISO_code)
df7.origin_code_type = np.where(np.logical_and(df7.artist_code_type2.isin([2]),df7.artist_ISO_code2.notnull()) , df7.artist_code_type2, df7.origin_code_type)

In [62]:
#Adding the country information for the rows that have their origin empty and artist_code_type2 = 1:
df7.origin_code = np.where(np.logical_and(df7.artist_code_type2.isin([1]), df7.origin_ISO_code.isnull()), df7.artist_area2, df7.origin_code)
df7.origin_name = np.where(np.logical_and(df7.artist_code_type2.isin([1]), df7.origin_ISO_code.isnull()), df7.artist_area_name2, df7.origin_name)
df7.origin_ISO_code = np.where(np.logical_and(df7.artist_code_type2.isin([1]), df7.origin_ISO_code.isnull()), df7.artist_ISO_code2, df7.origin_ISO_code)
df7.origin_code_type = np.where(np.logical_and(df7.artist_code_type2.isin([1]), df7.origin_ISO_code.isnull()), df7.artist_code_type2, df7.origin_code_type)

In [63]:
#We repeat step 2 for the cities in artist_area_name2:
cities_to_match2 = df7[df7['artist_code_type2'] == 3] #Select the cities to match
#We remove the duplicate city names:
cities_to_match2.drop_duplicates(subset='artist_area_name2', keep=False, inplace=True)
#We remove the columns that we don't need:
columns = ['group_id', 'release_group', 'credit_id', 'release_area',
       'release_area_name', 'release_ISO_code', 'release_code_type',
       'release_year', 'artist_id', 'artist_mbid', 'artist_name_x',
       'artist_area2', 'artist_code_type2',
       'artist_ISO_code2', 'origin_code', 'origin_name', 'origin_ISO_code',
       'origin_code_type']
cities_to_match2.drop(labels=columns, axis=1, inplace=True)
cities_to_match2.head()

/home/ainhoa/anaconda3/envs/kschool/lib/python3.7/site-packages/ipykernel_launcher.py:4: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-copy
  after removing the cwd from sys.path.


release_id artist_area_name2
173      1474213               Roy
618      1960646         Barbières
3206      992765         Wilbraham
3907     1983355          Moorpark
5836     2213232          Asnières

In [64]:
#And now we can do the merging with the cities dataframe:
cities_matched2 = pd.merge(cities_to_match2, cities, how='left', left_on='artist_area_name2', right_on='area_name')
cities_matched2.head(20)

release_id artist_area_name2    area_name        country country_ISO
0      1474213               Roy          Roy  United States          US
1      1960646         Barbières          NaN            NaN         NaN
2       992765         Wilbraham          NaN            NaN         NaN
3      1983355          Moorpark     Moorpark  United States          US
4      2213232          Asnières          NaN            NaN         NaN
5      1610325            Serang       Serang      Indonesia          ID
6       529227        Los Mochis   Los Mochis         Mexico          MX
7       949508           Danvers          NaN            NaN         NaN
8       614278        Dzerzhinsk   Dzerzhinsk         Russia          RU
9       118159             Ardee          NaN            NaN         NaN
10     1267435           Cuerden          NaN            NaN         NaN
11     1453340         Perleberg          NaN            NaN         NaN
12     2286341          Houilles          NaN            NaN         NaN
13     1202946            Tanabe          NaN            NaN         NaN
14     1572365            Suzhou          NaN            NaN         NaN
15     2116714           Findlay      Findlay  United States          US
16     1382280       Meadow Lake  Meadow Lake         Canada          CA
17     1216961          Jabalpur     Jabalpur          India          IN
18      292988       Chestertown  Chestertown  United States          US
19     1534701    Point Pleasant          NaN            NaN         NaN

In [65]:
#Now we can input this information into our main dataframe:
df8 = pd.merge(df7, cities_matched2, how='left', on='release_id')
df8.head()

release_id  group_id            release_group  credit_id  release_area  \
0     2163750   1962329                             2205562         240.0   
1     1846605   1713833                             1503027         240.0   
2     1714060   1609358    Beaux Soirs De Paris     1324142          73.0   
3     2265346   2042812                    Le 1     2291833         240.0   
4     1895266   1751021   M2Music HitDisc Vol. 1          1         222.0   

  release_area_name release_ISO_code  release_code_type release_year  \
0       [Worldwide]               XW                NaN   2014-01-01   
1       [Worldwide]               XW                NaN   2015-01-01   
2            France               FR                1.0   1995-01-01   
3       [Worldwide]               XW                NaN   2018-01-01   
4     United States               US                1.0   2006-01-01   

   artist_id  ... artist_code_type2 artist_ISO_code2  origin_code origin_name  \
0  1654312.0  ...               NaN              NaN          NaN         NaN   
1  1112115.0  ...               NaN              NaN          NaN         NaN   
2  1122795.0  ...               NaN              NaN          NaN         NaN   
3  1720981.0  ...               NaN              NaN          NaN         NaN   
4        1.0  ...               NaN              NaN          NaN         NaN   

   origin_ISO_code origin_code_type  artist_area_name2_y area_name country  \
0              NaN              NaN                  NaN       NaN     NaN   
1              NaN              NaN                  NaN       NaN     NaN   
2              NaN              NaN                  NaN       NaN     NaN   
3              NaN              NaN                  NaN       NaN     NaN   
4              NaN              NaN                  NaN       NaN     NaN   

  country_ISO  
0         NaN  
1         NaN  
2         NaN  
3         NaN  
4         NaN  

[5 rows x 24 columns]

In [66]:
#We input the info in the last columns into our origin columns:
df8.origin_code = np.where(df8.country_ISO.notnull(), df8.artist_area2, df8.origin_code)
df8.origin_name = np.where(df8.country_ISO.notnull(), df8.artist_area_name2_x, df8.origin_name)
df8.origin_ISO_code = np.where(df8.country_ISO.notnull(), df8.country_ISO, df8.origin_ISO_code)
df8.origin_code_type = np.where(df8.country_ISO.notnull(), df8.artist_code_type2, df8.origin_ISO_code)

In [67]:
#And now we can delete all the columns related to artist area2 and the ones generated in the last step:
remove = ['artist_area2', 'artist_area_name2_x', 'artist_code_type2','artist_ISO_code2','artist_area_name2_y', 'area_name', 'country','country_ISO']
df8.drop(labels=remove, axis=1, inplace=True)
df8.head()

release_id  group_id            release_group  credit_id  release_area  \
0     2163750   1962329                             2205562         240.0   
1     1846605   1713833                             1503027         240.0   
2     1714060   1609358    Beaux Soirs De Paris     1324142          73.0   
3     2265346   2042812                    Le 1     2291833         240.0   
4     1895266   1751021   M2Music HitDisc Vol. 1          1         222.0   

  release_area_name release_ISO_code  release_code_type release_year  \
0       [Worldwide]               XW                NaN   2014-01-01   
1       [Worldwide]               XW                NaN   2015-01-01   
2            France               FR                1.0   1995-01-01   
3       [Worldwide]               XW                NaN   2018-01-01   
4     United States               US                1.0   2006-01-01   

   artist_id                           artist_mbid    artist_name_x  \
0  1654312.0  d10d6441-dcc1-4202-93bf-0c0acf72913a         Soul Glo   
1  1112115.0  7b52c77b-1a34-439d-a285-3a7c69cb5b1a      Ben Bennett   
2  1122795.0  71b8451c-c10a-400e-9544-101f34ab2522  Soixante Étages   
3  1720981.0  a69efb5f-0b28-4328-8ff0-44d8d6f39755         TedeuzeM   
4        1.0  89ad4ac3-39f7-470e-963a-56509c546377  Various Artists   

   origin_code origin_name origin_ISO_code origin_code_type  
0          NaN         NaN             NaN              NaN  
1          NaN         NaN             NaN              NaN  
2          NaN         NaN             NaN              NaN  
3          NaN         NaN             NaN              NaN  
4          NaN         NaN             NaN              NaN

In [68]:
#For how many releases do we have the origin ISO code so far, now?
df8.origin_ISO_code.isnull().value_counts()

False    971572
True     533430
Name: origin_ISO_code, dtype: int64

### Data from the 1 million songs dataset

Between 2011 and 2012, there was a Music Information Retrieval challenge called "Million Song Dataset". The majority of the data contained was provided by The Echo Nest (today known as Spotify).

At the bottom of the following website, there are links to download the Dataset:

https://labrosa.ee.columbia.edu/millionsong/pages/getting-dataset

As we won't use the whole dataset (just some of the tables), you don't need to download them: they will be attached in the repo.

In [69]:
artists_locations = pd.read_csv('1M_songs/artist_location.csv',sep='<SEP>', header=None, engine='python')

In [73]:
artists_locations.columns = ['artist_id','lat','long','artist_name','location_name']
artists_locations.head()

artist_id       lat      long           artist_name  \
0  ARZGXZG1187B9B56B6 -16.96595 -61.14804          Endless Blue   
1  AR8K6F31187B99C2BC  46.44231 -93.36586               Go Fish   
2  ARHJJ771187FB5B581  51.59678  -0.33556  Screaming Lord Sutch   
3  ARJ8YLL1187FB3CA93  40.69626 -73.83301          Morton Gould   
4  ARYBAGV11ECC836DAC  43.58828 -79.64372        Crash Parallel   

                location_name  
0                  Santa Cruz  
1             Twin Cities, MN  
2  Harrow, Middlesex, England  
3           Richmond Hill, NY  
4                 Mississauga

In [74]:
#How many artist are there?
artists_locations['artist_id'].nunique()

13850

In this dataset, there is also another table which provides us with some extra information, especially the artist Musicbrainz's id (which will be very helpful to make the link with our main dataframe later).

In [75]:
metadata = pd.read_csv('1M_songs/track_metadata.csv',sep=',', header=0, engine='python', usecols=['artist_id','artist_mbid'])
metadata.head()

artist_id                           artist_mbid
0  ARYZTJS1187B98C555  357ff05d-848a-44cf-b608-cb34b5701ae5
1  ARMVN3U1187FB3A1EB  8d7ef530-a6fd-4f8f-b2e2-74aec765e0f9
2  ARGEKB01187FB50750  3d403d44-36ce-465c-ad43-ae877e65adc4
3  ARNWYLR1187B9B2F9C  12be7648-7094-495f-90e6-df4189d68615
4  AREQDTE1269FB37231                                   NaN

In [125]:
#We drop the rows withour artist_mbid (as we can't link them with our df)
metadata.dropna(subset=['artist_mbid'],axis=0, inplace=True)
#We merge artist_locations and metadata dataframes:
a = pd.merge(artists_locations,metadata,how='left',on='artist_id', copy=False)
a.dropna(subset=['artist_mbid'],axis=0, inplace=True)
a.head()

artist_id       lat      long   artist_name    location_name  \
0  ARZGXZG1187B9B56B6 -16.96595 -61.14804  Endless Blue       Santa Cruz   
1  ARZGXZG1187B9B56B6 -16.96595 -61.14804  Endless Blue       Santa Cruz   
2  AR8K6F31187B99C2BC  46.44231 -93.36586       Go Fish  Twin Cities, MN   
3  AR8K6F31187B99C2BC  46.44231 -93.36586       Go Fish  Twin Cities, MN   
4  AR8K6F31187B99C2BC  46.44231 -93.36586       Go Fish  Twin Cities, MN   

                            artist_mbid  
0  0bd9755c-c86d-431c-bc28-ef908b8a9821  
1  0bd9755c-c86d-431c-bc28-ef908b8a9821  
2  d4620364-82ec-4c34-9265-a2b72dfa8e3e  
3  d4620364-82ec-4c34-9265-a2b72dfa8e3e  
4  d4620364-82ec-4c34-9265-a2b72dfa8e3e

In [126]:
#We get rid of the duplicate rows:
a.drop_duplicates(subset='artist_id', inplace=True)
a.head()

artist_id       lat      long           artist_name  \
0   ARZGXZG1187B9B56B6 -16.96595 -61.14804          Endless Blue   
2   AR8K6F31187B99C2BC  46.44231 -93.36586               Go Fish   
33  ARHJJ771187FB5B581  51.59678  -0.33556  Screaming Lord Sutch   
64  ARJ8YLL1187FB3CA93  40.69626 -73.83301          Morton Gould   
78  ARYBAGV11ECC836DAC  43.58828 -79.64372        Crash Parallel   

                 location_name                           artist_mbid  
0                   Santa Cruz  0bd9755c-c86d-431c-bc28-ef908b8a9821  
2              Twin Cities, MN  d4620364-82ec-4c34-9265-a2b72dfa8e3e  
33  Harrow, Middlesex, England  e1079a78-75d4-4a1a-aef1-0be051386598  
64           Richmond Hill, NY  4db4e744-3007-4386-b87d-9653acfe0464  
78                 Mississauga  b0d85cf7-b73b-4a5d-bf31-a82493c3a8a8

As we can see above, the column "location_name" provides us with some geographical information but, for instance, in the first row, we don't really know the country where Santa Cruz is located.

Luckily, we have a pair of coordinates that we can use to retrieve more geographical detail for each row:

In [127]:
#We first create a new column called "coords" in which we'll gather both latitude and longitude:
a['coords'] = list(zip(a.lat, a.long))
coords = tuple(a['coords'].values.tolist())
#And now we use the reverse_geocoder utility to retrieve info for each pair of coordinates:
address = reverse_geocoder.search(coords)
a['address'] = address
a.head()

artist_id       lat      long           artist_name  \
0   ARZGXZG1187B9B56B6 -16.96595 -61.14804          Endless Blue   
2   AR8K6F31187B99C2BC  46.44231 -93.36586               Go Fish   
33  ARHJJ771187FB5B581  51.59678  -0.33556  Screaming Lord Sutch   
64  ARJ8YLL1187FB3CA93  40.69626 -73.83301          Morton Gould   
78  ARYBAGV11ECC836DAC  43.58828 -79.64372        Crash Parallel   

                 location_name                           artist_mbid  \
0                   Santa Cruz  0bd9755c-c86d-431c-bc28-ef908b8a9821   
2              Twin Cities, MN  d4620364-82ec-4c34-9265-a2b72dfa8e3e   
33  Harrow, Middlesex, England  e1079a78-75d4-4a1a-aef1-0be051386598   
64           Richmond Hill, NY  4db4e744-3007-4386-b87d-9653acfe0464   
78                 Mississauga  b0d85cf7-b73b-4a5d-bf31-a82493c3a8a8   

                                        coords  \
0                       (-16.96595, -61.14804)   
2                        (46.44231, -93.36586)   
33  (51.596779999999995, -0.33555999999999997)   
64             (40.696259999999995, -73.83301)   
78                       (43.58828, -79.64372)   

                                              address  
0   {'lat': '-16.43333', 'lon': '-60.9', 'name': '...  
2   {'lat': '46.53301', 'lon': '-93.71025', 'name'...  
33  {'lat': '51.58342', 'lon': '-0.3386', 'name': ...  
64  {'lat': '40.68149', 'lon': '-73.83652', 'name'...  
78  {'lat': '43.5789', 'lon': '-79.6583', 'name': ...

In [82]:
#Let's see how is this new infor formatted:
a['address'][0]

OrderedDict([('lat', '-16.43333'),
             ('lon', '-60.9'),
             ('name', 'Concepcion'),
             ('admin1', 'Santa Cruz'),
             ('admin2', ''),
             ('cc', 'BO')])

In [84]:
#What about the second row?
a['address'][2]

OrderedDict([('lat', '46.53301'),
             ('lon', '-93.71025'),
             ('name', 'Aitkin'),
             ('admin1', 'Minnesota'),
             ('admin2', 'Aitkin County'),
             ('cc', 'US')])

It looks like we would need the fields "admin1" and "cc" (which seems to contain the country ISO code). Let's extract that information for each row:

In [128]:
#We reset the index for the following loop to work:
a.reset_index(drop=True, inplace=True)

In [132]:
#We create 2 empty columns:
start = time.time()
a['state'] = np.nan
a['country_ISO'] = np.nan

#And fill them with the info we need:

for i in range(len(a)):
    address = list(a['address'][i].items())
    a['state'][i] = address[3][1]
    a['country_ISO'][i] = address[5][1]
end = time.time()
print(end-start)
#We check the result:
a.head()

/home/ainhoa/anaconda3/envs/kschool/lib/python3.7/site-packages/ipykernel_launcher.py:10: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-copy
  # Remove the CWD from sys.path while we load stuff.
/home/ainhoa/anaconda3/envs/kschool/lib/python3.7/site-packages/ipykernel_launcher.py:11: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-copy
  # This is added back by InteractiveShellApp.init_path()


3217.9600045681


artist_id       lat      long           artist_name  \
0  ARZGXZG1187B9B56B6 -16.96595 -61.14804          Endless Blue   
1  AR8K6F31187B99C2BC  46.44231 -93.36586               Go Fish   
2  ARHJJ771187FB5B581  51.59678  -0.33556  Screaming Lord Sutch   
3  ARJ8YLL1187FB3CA93  40.69626 -73.83301          Morton Gould   
4  ARYBAGV11ECC836DAC  43.58828 -79.64372        Crash Parallel   

                location_name                           artist_mbid  \
0                  Santa Cruz  0bd9755c-c86d-431c-bc28-ef908b8a9821   
1             Twin Cities, MN  d4620364-82ec-4c34-9265-a2b72dfa8e3e   
2  Harrow, Middlesex, England  e1079a78-75d4-4a1a-aef1-0be051386598   
3           Richmond Hill, NY  4db4e744-3007-4386-b87d-9653acfe0464   
4                 Mississauga  b0d85cf7-b73b-4a5d-bf31-a82493c3a8a8   

                                       coords  \
0                      (-16.96595, -61.14804)   
1                       (46.44231, -93.36586)   
2  (51.596779999999995, -0.33555999999999997)   
3             (40.696259999999995, -73.83301)   
4                       (43.58828, -79.64372)   

                                             address       state country_ISO  
0  {'lat': '-16.43333', 'lon': '-60.9', 'name': '...  Santa Cruz          BO  
1  {'lat': '46.53301', 'lon': '-93.71025', 'name'...   Minnesota          US  
2  {'lat': '51.58342', 'lon': '-0.3386', 'name': ...     England          GB  
3  {'lat': '40.68149', 'lon': '-73.83652', 'name'...    New York          US  
4  {'lat': '43.5789', 'lon': '-79.6583', 'name': ...     Ontario          CA

Note: the above loop took 55 minutes to run aprox.

In [134]:
#We drop the unnecessary columns:
a.drop(labels=['artist_id','lat','long', 'artist_name','coords','address'], axis=1, inplace=True)

In [135]:
#We input the retrieved information into our main dataframe:
df9 = pd.merge(df8, a, how='left', on='artist_mbid')
df9.columns

Index(['release_id', 'group_id', 'release_group', 'credit_id', 'release_area',
       'release_area_name', 'release_ISO_code', 'release_code_type',
       'release_year', 'artist_id', 'artist_mbid', 'artist_name_x',
       'origin_code', 'origin_name', 'origin_ISO_code', 'origin_code_type',
       'location_name', 'state', 'country_ISO'],
      dtype='object')

The column country ISO will be used as origin_ISO_code for the rows where the country isn't US, Canada or Australia. For these 3 countries, we need to create an extra column in which we retrieve also the subdivision.

To do so, we can use our areas_ISO dataframe:

In [141]:
areas_ISO[areas_ISO['code_type'] == 2]

area_id                                    area_name  code_type  \
25         1949                                    Borovnica        2.0   
74         1969                                    Dravograd        2.0   
113        2205                                    Agio Oros        2.0   
165        4695                                         Roma        2.0   
185        1950                                        Bovec        2.0   
221        1951                                         Brda        2.0   
222         306                                     Virginia        2.0   
228         261                                     Maryland        2.0   
230        2004                                       Litija        2.0   
231        2113                                    Mirna Peč        2.0   
233        2038                                     Postojna        2.0   
234        2153             Sveti Jurij v Slovenskih goricah        2.0   
235        2074                                      Trebnje        2.0   
236        2001                                        Laško        2.0   
246         268                                  Connecticut        2.0   
248         265                                      Arizona        2.0   
249         267                                     Colorado        2.0   
252         264                                     Arkansas        2.0   
255        2206               Anatoliki Makedonia kai Thraki        2.0   
260         271                                      Florida        2.0   
261         263                                      Alabama        2.0   
263         266                                   California        2.0   
265        4696                                       Rimini        2.0   
274         272                                      Georgia        2.0   
275         273                                       Hawaii        2.0   
276         274                                         Iowa        2.0   
277         275                                        Idaho        2.0   
279         276                                     Illinois        2.0   
280         277                                      Indiana        2.0   
281         278                                       Kansas        2.0   
282         279                                     Kentucky        2.0   
283         280                                    Louisiana        2.0   
284         281                                Massachusetts        2.0   
285         282                                        Maine        2.0   
286         283                                     Michigan        2.0   
287         284                                    Minnesota        2.0   
289        2242                                    Nisporeni        2.0   
290        2279                                 Demir Kapija        2.0   
291        2281                                       Dojran        2.0   
292        2554                               Hamgyŏng-namdo        2.0   
293        4560                                        Jambi        2.0   
294        1985                                     Jesenice        2.0   
295        2361                            Volyns'ka Oblast'        2.0   
296        2190                                       Shumen        2.0   
297        2006                                       Ljubno        2.0   
298        2324                                 Sveti Nikole        2.0   
299        2409                         Kemerovskaya oblast'        2.0   
301        1992                                      Kočevje        2.0   
302        2008                                      Logatec        2.0   
303        4835                                      Mchinji        2.0   
304        2018                                       Mežica        2.0   
305        2115                                    Podlehnik        2.0   
306        2040                  

In [142]:
df10 = pd.merge(df9, areas_ISO, how='left', left_on='state', right_on='area_name')
df10.columns

Index(['release_id', 'group_id', 'release_group', 'credit_id', 'release_area',
       'release_area_name', 'release_ISO_code', 'release_code_type',
       'release_year', 'artist_id', 'artist_mbid', 'artist_name_x',
       'origin_code', 'origin_name', 'origin_ISO_code', 'origin_code_type',
       'location_name', 'state', 'country_ISO', 'area_id', 'area_name',
       'code_type', 'ISO_code'],
      dtype='object')

Now we can do the final merge: 

- For the rows that have the column 'origin_ISO_code empty and 'ISO code' not empty: we keep the ISO code as origin_ISO_code (those will be rows belonging to USA, Canada and Australia.
- For the rows that have the column 'origin_ISO_code empty and 'country_ISO' not empty: we keep the country_ISO as origin_ISO code

In [144]:
#First for USA, Canada and Australia:
df10.origin_ISO_code = np.where(np.logical_and(df10.ISO_code.notnull(),df10.origin_ISO_code.isnull()),df10.ISO_code,df10.origin_ISO_code)
df10.origin_name = np.where(np.logical_and(df10.ISO_code.notnull(),df10.origin_ISO_code.isnull()),df10.area_name,df10.origin_name)
df10.origin_code_type = np.where(np.logical_and(df10.ISO_code.notnull(),df10.origin_ISO_code.isnull()),df10.code_type,df10.origin_code_type)
#Then, for the rest:
df10.origin_ISO_code = np.where(np.logical_and(df10.country_ISO.notnull(),df10.origin_ISO_code.isnull()),df10.country_ISO,df10.origin_ISO_code)
df10.origin_name = np.where(np.logical_and(df10.country_ISO.notnull(),df10.origin_ISO_code.isnull()),df10.area_name,df10.origin_name)
df10.origin_code_type = np.where(np.logical_and(df10.country_ISO.notnull(),df10.origin_ISO_code.isnull()),1,df10.origin_code_type)

In [145]:
#We can drop the unnecesary columns:
columns = ['location_name','state', 'country_ISO', 'area_id', 'area_name', 'code_type', 'ISO_code']
df10.drop(labels=columns, axis=1, inplace=True)

In [149]:
#Dropping duplicated lines after the merging:
df10.drop_duplicates(subset=['release_id'],keep='first', inplace=True)

In [150]:
#For how many releases do we have the origin ISO code now, after this last step?
df10.origin_ISO_code.isnull().value_counts()

False    977235
True     522379
Name: origin_ISO_code, dtype: int64

So, before this last step using data from 1 million songs, we had 971.572 releases with ISO code, now we have an extra 5663 releases with that info.

### Data from Wikidata Query with SPARQL

https://query.wikidata.org/

1) Musicians

SELECT ?musician ?musicianLabel ?genre ?genreLabel ?MusicBrainz_artist_ID ?place_of_birth ?place_of_birthLabel WHERE {
  SERVICE wikibase:label { bd:serviceParam wikibase:language "[AUTO_LANGUAGE],en". }
  ?musician wdt:P106 wd:Q639669.
  OPTIONAL { ?musician wdt:P136 ?genre. }
  OPTIONAL { ?musician wdt:P434 ?MusicBrainz_artist_ID. }
  OPTIONAL { ?musician wdt:P19 ?place_of_birth. }
}


--> Export to csv file: query_wikidata_musicians.csv

2) Singers

SELECT ?musician ?musicianLabel ?genre ?genreLabel ?MusicBrainz_artist_ID ?place_of_birth ?place_of_birthLabel WHERE {
  SERVICE wikibase:label { bd:serviceParam wikibase:language "[AUTO_LANGUAGE],en". }
  ?musician wdt:P106 wd:Q177220.
  OPTIONAL { ?musician wdt:P136 ?genre. }
  OPTIONAL { ?musician wdt:P434 ?MusicBrainz_artist_ID. }
  OPTIONAL { ?musician wdt:P19 ?place_of_birth. }
}

--> Export to csv file: query_wikidata_singers.csv

3) Bands

SELECT ?band ?bandLabel ?genre ?genreLabel ?MusicBrainz_artist_ID ?location_of_formation ?location_of_formationLabel WHERE {
  SERVICE wikibase:label { bd:serviceParam wikibase:language "[AUTO_LANGUAGE],en". }
  ?band wdt:P31 wd:Q215380.
  OPTIONAL { ?band wdt:P136 ?genre. }
  OPTIONAL { ?band wdt:P434 ?MusicBrainz_artist_ID. }
  OPTIONAL { ?band wdt:P740 ?location_of_formation. }
}

--> Export to csv file: query_wikidata_bands.csv

In [3]:
#Open the files and load them into dataframes with the same column names (to match with our main dataframe later):
musicians = pd.read_csv('wikidata/query_wikidata_musicians.csv',sep=',', encoding='utf-8', usecols=[4,6])
musicians.rename(columns={'MusicBrainz_artist_ID':'artist_mbid','place_of_birthLabel':'origin_name'}, inplace=True)
singers = pd.read_csv('wikidata/query_wikidata_singers.csv',sep=',', encoding='utf-8', usecols=[4,6])
singers.rename(columns={'MusicBrainz_artist_ID':'artist_mbid','place_of_birthLabel':'origin_name'}, inplace=True)
bands = pd.read_csv('wikidata/query_wikidata_bands.csv',sep=',', encoding='utf-8', usecols=[4,6])
bands.rename(columns={'MusicBrainz_artist_ID':'artist_mbid','location_of_formationLabel':'origin_name'}, inplace=True)

In [152]:
bands.head()

artist_mbid origin_name
0  f26c72d3-e52c-467b-b651-679c73d8e1a7  Sacramento
1  f26c72d3-e52c-467b-b651-679c73d8e1a7  Sacramento
2  f26c72d3-e52c-467b-b651-679c73d8e1a7  Sacramento
3  a3cb23fc-acd3-4ce0-8f36-1e5aa6a18432      Dublin
4  a3cb23fc-acd3-4ce0-8f36-1e5aa6a18432      Dublin

In [4]:
#Now we can concatenate the 3 dataframes into one:
wiki_df = pd.concat([musicians, singers, bands])
wiki_df.head()

artist_mbid            origin_name
0                                   NaN  Cherbourg-en-Cotentin
1  b972f589-fb0e-474e-b64a-803b0364fa75               Salzburg
2  b972f589-fb0e-474e-b64a-803b0364fa75               Salzburg
3  b972f589-fb0e-474e-b64a-803b0364fa75               Salzburg
4  b972f589-fb0e-474e-b64a-803b0364fa75               Salzburg

In [154]:
len(wiki_df)

226926

In [5]:
#We can directly drop the rows which don't have a musicbrainz's id (we need and ID to join with our main df):
wiki_df.dropna(subset=['artist_mbid'], axis=0, inplace=True)

In [6]:
#Let's see how many artists we have:
wiki_df['artist_mbid'].nunique()

96110

In [7]:
#Drop duplicated artist_mbid:
wiki_df.drop_duplicates(subset=['artist_mbid'],keep='first', inplace=True)

In [8]:
#What kind of information do we have in the column origin_name?:
wiki_df.origin_name.value_counts()

New York City            1273
Los Angeles              1209
London                    995
Tokyo                     750
Paris                     440
Chicago                   436
Brooklyn                  390
Seoul                     376
Philadelphia              348
Toronto                   333
Berlin                    324
Stockholm                 323
San Francisco             289
Seattle                   282
Boston                    268
Moscow                    267
California                266
Montreal                  248
Detroit                   248
Oslo                      219
Rome                      215
Rio de Janeiro            212
Helsinki                  212
Vienna                    201
Istanbul                  200
Atlanta                   197
Liverpool                 196
Buenos Aires              188
Manchester                187
Nashville                 187
                         ... 
Niebüll                     1
Isernia                     1
Indian Hil

It looks like we have city names, so we can use our "cities" dataframe to retrieve the country ISO codes:

In [12]:
wiki_ISO = pd.merge(wiki_df, cities, how='left', left_on='origin_name', right_on='area_name')
wiki_ISO.head()

artist_mbid  origin_name    area_name  \
0  b972f589-fb0e-474e-b64a-803b0364fa75     Salzburg     Salzburg   
1  b58165ba-ac55-49a1-8855-caf16c68f5f2         Sète          NaN   
2  d135874d-9cae-4fef-97e3-36acbd9f5a26      Chicago      Chicago   
3  75167b8b-44e4-407b-9d35-effe87b223cf      Toronto      Toronto   
4  4b585938-f271-45e2-b19a-91c634b5e396  Bexleyheath  Bexleyheath   

          country country_ISO  
0         Austria          AT  
1             NaN         NaN  
2   United States          US  
3          Canada          CA  
4  United Kingdom          GB

In order to retrieve the ISO codes for USA, Canada and Australia, we can use our areas_ISO dataframe too:

In [21]:
wiki_ISO1 = pd.merge(wiki_ISO, areas_ISO[['area_name','ISO_code']], how='left', on='area_name')
wiki_ISO1.head()

artist_mbid origin_name area_name        country  \
0  b972f589-fb0e-474e-b64a-803b0364fa75    Salzburg  Salzburg        Austria   
1  b972f589-fb0e-474e-b64a-803b0364fa75    Salzburg  Salzburg        Austria   
2  b972f589-fb0e-474e-b64a-803b0364fa75    Salzburg  Salzburg        Austria   
3  b58165ba-ac55-49a1-8855-caf16c68f5f2        Sète       NaN            NaN   
4  d135874d-9cae-4fef-97e3-36acbd9f5a26     Chicago   Chicago  United States   

  country_ISO ISO_code  
0          AT      NaN  
1          AT      NaN  
2          AT      NaN  
3         NaN      NaN  
4          US      NaN

In [22]:
#Drop duplicated artist_mbid:
wiki_ISO1.drop_duplicates(subset=['artist_mbid'],keep='first', inplace=True)
#And delete the extra column "origin_name"
wiki_ISO1.drop(labels='origin_name', axis=1, inplace=True)

In [212]:
##CHECKPOINT: EXPORT DF10:
df10.to_csv('df10.csv', sep='\t', index=False, encoding='utf-8' )

In [23]:
#START FROM CHECKPOINT: IMPORT DF10
df10 = pd.read_csv('df10.csv', sep='\t', header=0, encoding='utf-8')

In [24]:
#And we can merge that information into our main dataframe:
df11 = pd.merge(df10, wiki_ISO1, how='left', on='artist_mbid')
df11.columns

Index(['release_id', 'group_id', 'release_group', 'credit_id', 'release_area',
       'release_area_name', 'release_ISO_code', 'release_code_type',
       'release_year', 'artist_id', 'artist_mbid', 'artist_name_x',
       'origin_code', 'origin_name', 'origin_ISO_code', 'origin_code_type',
       'area_name', 'country', 'country_ISO', 'ISO_code'],
      dtype='object')

Now, as we did in previous steps, we can input the information in these new columns into our origin columns (first, for the rows related to USA, Canada and Australia, then for the rest):

In [25]:
#First for USA, Canada and Australia:
df11.origin_ISO_code = np.where(np.logical_and(df11.ISO_code.notnull(),df11.origin_ISO_code.isnull()),df11.ISO_code,df11.origin_ISO_code)
df11.origin_name = np.where(np.logical_and(df11.ISO_code.notnull(),df11.origin_ISO_code.isnull()),df11.area_name,df11.origin_name)
df11.origin_code_type = np.where(np.logical_and(df11.ISO_code.notnull(),df11.origin_ISO_code.isnull()),2,df10.origin_code_type)
#Then, for the rest:
df11.origin_ISO_code = np.where(np.logical_and(df11.country_ISO.notnull(),df11.origin_ISO_code.isnull()),df11.country_ISO,df11.origin_ISO_code)
df11.origin_name = np.where(np.logical_and(df11.country_ISO.notnull(),df11.origin_ISO_code.isnull()),df11.area_name,df11.origin_name)
df11.origin_code_type = np.where(np.logical_and(df11.country_ISO.notnull(),df11.origin_ISO_code.isnull()),1,df11.origin_code_type)

In [26]:
#Drop unnecessary columns:
columns = ['area_name','country','country_ISO','ISO_code']
df11.drop(labels=columns, axis=1, inplace=True)

In [27]:
#For how many releases do we have the origin ISO code now, after this last step?
df11.origin_ISO_code.isnull().value_counts()

False    984158
True     515456
Name: origin_ISO_code, dtype: int64

We have retrieved the information for an extra 6.923 releases in this last step, thanks to Wikidata Query.

As we have retrieved geographical data from 4 different sources already, we need to analyze what we have left.

Who are the artists for which we don't have any origin information?

In [28]:
unknown_area = df11[df11['origin_ISO_code'].isnull()]

In [29]:
#How many artists are there?
unknown_area['artist_mbid'].nunique()

188359

So, according to the above line, we have 188.359 artists with unknown or vague origin. Let's have a closer look:

In [30]:
unknown_artist = unknown_area.groupby('artist_name_x').count().sort_values('release_id',ascending=False)
unknown_artist.head(1000)

release_id  group_id  release_group  \
artist_name_x                                                          
Various Artists                      134847    134847         134847   
Berliner Philharmoniker                 550       550            550   
[language instruction]                  278       278            278   
Dwelling of Duels                       180       180            180   
[nature sounds]                         170       170            170   
Tom Jones                               160       160            160   
Michael Koser                           139       139            139   
Peerless Orchestra                      122       122            122   
Edison Concert Band                     115       115            115   
Daniel Menche                           115       115            115   
Minniva                                 114       114            114   
[dialogue]                              112       112            112   
Bibi & Tina                             109       109            109   
Eminem                                  108       108            108   
[no artist]                             108       108            108   
HasenChat Music                         100       100            100   
Celer                                    99        99             99   
How Did This Get Made?                   98        98             98   
Edward M. Favor                          97        97             97   
Samuel Sagan                             95        95             95   
Jonathan Parecki                         94        94             94   
Tim Timebomb                             90        90             90   
Les Schtroumpfs                          89        89             89   
Dan W. Quinn                             86        86             86   
Rank 197                                 85        85             85   
Diverse System                           82        82             82   
KMFDM                                    82        82             82   
Massive Attack                           80        80             80   
Nas                                      79        79             79   
Ryan Preston                             74        74             74   
...                                     ...       ...            ...   
Dries Roelvink                           17        17             17   
Chris Corsano                            17        17             17   
Amorf Ördögök                            17        17             17   
Black Sun Productions                    17        17             17   
Werner Müller and His Orchestra          17        17             17   
Shigeto                                  17        17             17   
Amp                                      17        17             17   
Phoenix #2772                            17        17             17   
Rafael Canaro                            17        17             17   
Sonny Vincent                            17        17             17   
Celldöd                                  17        17             17   
L'Archibudelli                           17        17             17   
Maxo                                     17        17             17   
Woody McBride                            17        17             17   
Noto                                     17        17             17   
The Vandermark 5                         17        17             17   
Nytrix                                   17        17             17   
The Bamboos                              17        17             17   
Hex                                      17        17             17   
Rüdiger Lorenz                           17        17             17   
Photophob                                17        17             17   
Hellberg                                 17        17             17   
Seht                                     17        17             17   
N

In [182]:
#From what we can see above, the category "Various Artists" has many releases assigned:
df11[df11['artist_name_x']=='Various Artists']

release_id  group_id  \
4           1895266   1751021   
26           356044     14028   
41          1623578   1539062   
44           475440    785494   
45            62055     28102   
46          1053661   1078102   
47            62061    147591   
48          1447852    147591   
49          1012140    955241   
50          2319247   2084339   
51          2327624   2090989   
53           725914    981951   
69           686550    952517   
70          1630852   1544917   
83          1572461   1498671   
193          510871    815185   
194         2241261   2024009   
195         1582410   1506660   
196         1766351   1651172   
208         1350888   1316456   
209          178590    363395   
211          402912    725927   
212         1766782   1651511   
214          404062    726818   
215          412730    733697   
216          117141    489665   
217         1563701   1491838   
218         1563690   1491828   
219          127131    497868   
220          597713    230258   
221         1489657   1430380   
222           27281     92007   
223          804099   1044425   
224          616073    897598   
225          175209    535717   
226          558349    853335   
227          718542    976639   
228          170562    532005   
231         1079850   1099410   
234          192133    257320   
236         1859994   1724263   
244          643165    918166   
245          266373    613611   
246          643163    918163   
247         2158299   1957818   
261         2142036   1944551   
266         2136733   1940281   
276         2154803   1954915   
298          695486    959137   
299          815395   1053025   
301          494614    404672   
302          494615    404672   
527         1696475   1595501   
532         1244270   1231951   
546         2258755   2037508   
550         1921996   1771758   
559         1666943   1572776   
560         1733488   1624804   
561         1851437   1717709   
585         1665198   1526696   
590         1885508   1743604   
602         1715569   1610630   
603         1741986   1631577   
604         1886150   1744091   
605         1964229   1804542   
606         1987806   1822815   
607         1912195   1764056   
608         2013746   1843376   
610         1341778   1292582   
611         1320062   1292582   
623         1572647   1498815   
637         2119677   1926837   
639         2095250   1907984   
686         1871830   1733169   
707         1667675   1573395   
713         2277681   2052377   
716         2140880   1943579   
729         1636380   1549049   
743         1680869   1583498   
744         1179685   1179216   
807         2259869   2038439   
812         1926616   1775441   
813         1920710   1770681   
821         1840768   1709371   
836         2294251   2065088   
837         1787503   1668274   
838         1772117   1655788   
839         1443992   1389614   
840         1672256   1577046   
841         1984321   1820177   
842         1749363   1637611   
844         2085678   1900344   
851         1063584   1085955   
860         1703879   1601355   
864         2273687   2049193   
865         2268940   2045532   
899         1858097   1722728   
900         2378142   2132268   
908         1206048   1200392   
962           62183    409659   
1021         803237   1043713   
1022        1608677   1043713   
1026          42723    360786   
1027         149452    515813   
1067        1280010   1240524   
1119         555669    851339   
1135         920178    303155   
1136        1224130   1215417   
1137        2255960   2035236   
1138        2256493   2035663   
1139        2256506   2035673   
1140        2256518   2035681   
1141         370569    699384   
1142        1605034   1524122   
1143        2322750   2087068   
1144         128603    499316   
1167         465018    590695   
1168        2135911   1939634   
1169        1032069    637798   
1170         952153    373387   
1171         100

If we look in detail into these releases, we can see that most of them are music compilations (hence the generic category "Various Artists"). As they are music compilations, that means that the tracks included were originally released before by their genuine author, so we shouldn't take them into account (to avoid duplicates). Also, as we don't have an artist name for them, it will be impossible to retrieve the origin.

We will delete those rows from our dataframe later.

Let's analyze more in detail who are the rest of artists that have many releases, and decide what to do with them.

In [183]:
#Unknown artist:
df11[df11['artist_name_x']=='[unknown]']

release_id  group_id  \
7287         546135    843736   
8817         557295    852580   
9663        1232110   1222115   
9664         665743    936259   
9817        1235032   1224582   
9918         638247    914460   
10852       1208592   1202487   
11319        686485    952465   
11705       1247647   1234682   
16973       1015709    616974   
24882        652504    925618   
25162       1120161   1131958   
25223        507071    812060   
25406        718072    976309   
27709       1076239   1096301   
27736       1076251   1096313   
28521       1803794   1680861   
28648       2251694   2032015   
29907        802135   1042815   
32043       1770134   1654219   
32064       1076245   1096307   
32072        306795    505882   
32288        834578    343638   
32303        441061    757278   
33466       1621932   1537731   
33479        295640    636878   
38222       1141187   1149295   
38412        171852     97395   
38565       1406338    166773   
41740       1899225   1753979   
42342        723303    980024   
44820        170600    532082   
50770        385441    711393   
50857        385379    711356   
52826       1621937   1537734   
55628        790966   1034124   
55629       1279385   1260311   
58412       2144016   1946077   
61001       2266934   2043997   
63270        307361     76734   
63609       1606327   1525151   
64228        611031    893833   
64476        689638      7769   
64533        745216    997430   
68738        386900    712566   
68739        386938    712606   
70650       1601721   1521568   
71897        323081    661055   
76753       1421635   1372120   
77706        975819    461533   
77707        675700    944055   
77709       1830415   1701189   
77722       1739170    944055   
77727       1738478   1628717   
82614        386921    712589   
84897        386885    712490   
85039       1958720   1800489   
85040       1958725   1800492   
88623       1733372   1624705   
88625       1567999   1495260   
88976        385389    711361   
89143       1838622   1707684   
92442        458587    771506   
93008       1432362   1380718   
94321        386894    712560   
94583        386954    712622   
96589        620485    900996   
96590        620489    901000   
96591        620490    901001   
96592        620491    901002   
96593        620492    901003   
96993        407491    729517   
96994        407332    729380   
96995        407498    729524   
96996        407340    729386   
97892        534901    834615   
98407        352585    684987   
99831        802138   1042818   
101418       507473    812410   
101734      2117215    649710   
106387      1559312   1488484   
107203       386767    712486   
107430      1590042   1512512   
108804      1456055   1399200   
109961       385409    711372   
114651      2324415   2088450   
115518       414657    735229   
115519       567666    860313   
116418       820311   1056828   
116492      1621939   1537736   
116730       474401    735836   
116987      1911548   1763576   
117765       386946    712614   
118259       386823    712511   
119435      2028978   1855210   
124886      1700686   1598855   
124968       578111    868183   
128463      1803383   1680528   
130317       892915    166244   
131435       746867    998816   
132336      2134733   1938703   
135209       284633    628307   
137457      1903352   1757196   
137838      1903337   1757181   
139822       598480    883678   
140364       965380    422006   
141172      1105183   1119601   
142649       625578    904811   
142690      1978769   1815786   
143978       386859    712527   
145074      1837100   1706474   
145821      2158522   1958007   
145840       155061    520242   
147040      1504867   1444422   
147767       386951    712619   
151189       317401    656383   
152181      1837414   1706707   
153648      2207655   1997677   
157000       386805    712503   
159464       386918    712586   
166291      1570

The category "unknown" seems to contain music compilations too.

In [184]:
#"Language instruction" artist:
df11[df11['artist_name_x']=='[language instruction]']

release_id  group_id  \
11186        821781   1057780   
11187        822699   1058470   
30861        536732    836303   
51254       1921485   1771345   
51811       1920797   1770754   
73778       2107126   1916950   
78295        685879    731447   
81802       1381788   1341586   
82122       1921562   1771391   
100674      1921270   1771164   
102318       630154    908206   
102319       630138    908192   
102320      1228950   1219452   
104311      1921572   1771400   
104312      1921489   1771348   
112036      1921584   1771412   
112111      1920817   1770774   
112230      1920800   1770757   
112231      1920798   1770755   
112232      1920805   1770762   
112233      1920475   1770482   
112234      1921491   1771350   
112235      1921552   1771383   
112236      1920804   1770761   
112238      1920818   1770775   
112239      1920814   1770771   
112240      1920802   1770759   
112241      1920480   1770485   
112242      1920451   1770461   
112243      1920481   1770486   
112244      1920469   1770476   
112245      1920811   1770768   
112246      1920497   1770501   
112248      1920786   1770745   
112249      1921267   1771161   
125331      2014765   1844091   
125332      2014773   1844098   
125333       475724    785748   
125334       478425    787954   
136211       424205    743286   
147904       500267    806432   
147905      1666738   1572611   
151743      1856198   1721247   
153551      1921581   1771409   
176673       361228    691457   
184977      1921576   1771404   
231742      1920792   1770750   
237484      1921582   1771410   
248533      1920472   1770479   
255066      1920815   1770772   
278640      1921543   1771375   
278641      1920824   1770781   
306608       677095    945175   
310424       798635   1040421   
312230      1920810   1770767   
320683      1920794   1770751   
342732       825118   1060439   
342733      1107637   1121619   
342736      1169168   1170844   
350010       376354    704217   
350011       403893    726680   
350936       853354   1028371   
352092      2033014   1858490   
352093      2033035   1858506   
356198      1924499   1773666   
356199      2024784   1773666   
358091      1921548   1771380   
361594       688016    953472   
376411      1099755   1111419   
376415      1378040   1338477   
376416       450585    765098   
376523      1745252   1634291   
376524      1739692   1629724   
376525      1974677   1812634   
403222      1920453   1770463   
403494      1920822   1770779   
403621      1921561   1771390   
406104       402551    725573   
407023      1920788   1770746   
409942      1921550   1771381   
414122       786312   1030424   
416331      1236487   1225772   
435003      1236592   1225856   
435092       283506    627448   
438083       183212    542674   
438143       767205   1015266   
438144       767756   1015698   
438145       767771   1015709   
438146       767782   1015717   
438147       767793   1015720   
438281       909943    766770   
456947       502359    808207   
456948       557483    852724   
457862       546316    843845   
457863       547435    844694   
457864       547448    844707   
457865       719321    977159   
457866       719327    977171   
457911       759415   1009334   
457917       630672    908612   
460727      1920471   1770478   
465648      1920470   1770477   
484475      1817620   1691430   
484476      1818484   1692086   
484477      1818330   1691962   
484496      1921564   1771392   
506323      1921542   1771374   
525855      1724248   1617519   
530336      1920808   1770765   
531631      1106145   1120387   
536115      1921540   1771372   
536868      1920486   1770491   
538554       519749    251752   
576368       259244    607521   
583023       409803    731465   
587274      1920442   1770455   
588550      1921541   1771373   
591523      1921553   1771384   
594996       436837    753713   
595129       858858    862256   
595145       687

As its name suggests, these releases are language courses recorded, so they are not music and they are out of our scope too.

The same would apply to the categories [nature sounds], [dialogue] or [christmas music].

We can now delete from our dataframes all these cathegories, and see what we have left.

In [31]:
#In our main dataframe:
labels = ['[nature sounds]','[dialogue]','[christmas music]', 'Various Artists','[unknown]','[language instruction]']
df11.artist_name_x = np.where(df11.artist_name_x.isin(labels), np.nan, df11.artist_name_x)
df11.dropna(subset=['artist_name_x'], axis=0, inplace=True)

In [43]:
#In our unknown_area dataframe:
unknown_area.artist_name_x = np.where(unknown_area.artist_name_x.isin(labels), np.nan, unknown_area.artist_name_x)
unknown_area.dropna(subset=['artist_name_x'], axis=0, inplace=True)

/home/ainhoa/anaconda3/envs/kschool/lib/python3.7/site-packages/pandas/core/generic.py:5096: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-copy
  self[name] = value
/home/ainhoa/anaconda3/envs/kschool/lib/python3.7/site-packages/ipykernel_launcher.py:3: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-copy
  This is separate from the ipykernel package so we can avoid doing imports until


In [37]:
#So after this deletion of some releases, how many do we have left to retrieve the origin?
df11.origin_ISO_code.isnull().value_counts()

False    982785
True     379823
Name: origin_ISO_code, dtype: int64

In [41]:
#And how many artists do they represent?
unknown_area.artist_mbid.nunique()

188356

In [46]:
#Wich are the ones that produce the most?
unknown_artist = unknown_area.groupby('artist_name_x').count().sort_values('release_id',ascending=False)
unknown_artist.head(1000)

release_id  group_id  release_group  \
artist_name_x                                                             
Berliner Philharmoniker                    550       550            550   
Dwelling of Duels                          180       180            180   
Tom Jones                                  160       160            160   
Michael Koser                              139       139            139   
Peerless Orchestra                         122       122            122   
Edison Concert Band                        115       115            115   
Daniel Menche                              115       115            115   
Minniva                                    114       114            114   
Bibi & Tina                                109       109            109   
[no artist]                                108       108            108   
Eminem                                     108       108            108   
HasenChat Music                            100       100            100   
Celer                                       99        99             99   
How Did This Get Made?                      98        98             98   
Edward M. Favor                             97        97             97   
Samuel Sagan                                95        95             95   
Jonathan Parecki                            94        94             94   
Tim Timebomb                                90        90             90   
Les Schtroumpfs                             89        89             89   
Dan W. Quinn                                86        86             86   
Rank 197                                    85        85             85   
KMFDM                                       82        82             82   
Diverse System                              82        82             82   
Massive Attack                              80        80             80   
Nas                                         79        79             79   
Ryan Preston                                74        74             74   
Dead Eye Darter                             74        74             74   
Marc Gruppe                                 73        73             73   
Night Vale Presents                         72        72             72   
OverClocked ReMix                           72        72             72   
...                                        ...       ...            ...   
Shigeto                                     17        17             17   
Amorf Ördögök                               17        17             17   
Blown Out                                   17        17             17   
Celldöd                                     17        17             17   
Distimia                                    17        17             17   
Tellison                                    17        17             17   
Antoni Maiovvi                              17        17             17   
zahqo                                       17        17             17   
R. K. Franklin                              17        17             17   
Cloud Mac                                   17        17             17   
Star Anna                                   17        17             17   
Go-qualia                                   17        17             17   
Phoenix #2772                               17        17             17   
Deutsche Kammerphilharmonie Bremen          17        17             17   
Dasoul                                      17        17             17   
Lil Pump                                    17        17             17   
Dan Mason ダン·メイソン                           17        17             17   
Earthless                                   17        17             17   
Stiller Has                                 17        17             17   
Photophob                                   17        17             17   
Fatal Friction                              17        17     

In [51]:
df11[df11['artist_name_x'] == 'Berliner Philharmoniker']

release_id  group_id  \
7266        1880145   1739508   
9414        1894928   1052100   
9426        1894967   1052100   
9458        1895039   1052100   
9814        2244651   2026726   
27200        461081    773437   
30903        196588    498346   
31969        201571    442660   
31970        974264    386285   
33090       2213987    481592   
33091        362151    481592   
33327        354031   1508207   
33328       1607602   1508207   
34150        618639    899538   
35345        249456    600004   
36292       1315494    704146   
36297        232785    584907   
36298       1104921   1119405   
36300        234861    586761   
36313       2351459   2109961   
61476        796580   1038750   
61480       1469617     36959   
61495       1676820   1038750   
61506       1578019   2029227   
68503       2274495    913452   
70827        189140     85502   
81473       2256782    913452   
81504        455515    107927   
81511       1913217    913452   
81517       1391040    893876   
...             ...       ...   
1332383     1648255   1558531   
1332523     1687657   1588782   
1332550      709008     87492   
1332551      238015     87492   
1332552     2039360     54057   
1332557      249040    268521   
1332558     1367866    268521   
1332597      709007     87492   
1332606     1923472   1378411   
1332844     1269308    658722   
1332852     1229797   1220127   
1332853     1033398    787247   
1332856     1935869   1782659   
1332871     2131884   1936441   
1332881     1897058    658722   
1332910     1429506   1378411   
1335408      601758    886116   
1347070     1990849   1825324   
1347071      752129   1003365   
1349816     2132174   1936661   
1350832      915394    580648   
1350848      228092    580648   
1350859     2321459   1936661   
1350874     1300491   1277043   
1350908      429135    747368   
1357165     1581627   1506064   
1375294     1426441   1375898   
1421031     2072725   1051769   
1443733      480118    164298   
1468289     2088633   1872466   

                                             release_group  credit_id  \
7266                      100 Best Berliner Philharmoniker      64981   
9414     111 Years of Deutsche Grammophon: The Collecto...    1862166   
9426     111 Years of Deutsche Grammophon: The Collecto...    1058583   
9458     111 Years of Deutsche Grammophon: The Collecto...    1862486   
9814                                12 Londoner Symphonien    2275446   
27200                              3 Symphonies / The Rock    1337011   
30903                                        46 Symphonien    1106042   
31969                                         5. Symphonie    1382320   
31970                     5. Symphonie / Kindertotenlieder    1115711   
33090                                 6 "Paris" Symphonies    1499235   
33091                               6 "Pariser" Symphonien    1499235   
33327                                         6 Symphonien    1452684   
33328                                         6 Symphonien    1452618   
34150                                           7 Concerti    1013937   
35345                                         8 Symphonies    1484232   
36292                                         9 Symphonien     976419   
36297                                         9 Symphonien    1189390   
36298                                         9 Symphonien    1189747   
36300                            9 Symphonien / Ouvertüren    1217221   
36313                                         9 Symphonies    1418416   
61476                                               Adagio    1114107   
61480                                               Adagio     973250   
61495                                               Adagio    1553873   
61506                                             Adagio 2     973250   
68503    Ainsi Parlait Zarathoustra / Till L'Espiègle, ...    1937949   
70827                  Albinoni: Adagio / Pachelbel: Canon    10

# SEGUIR DESDE AQUI: VOLVER A CRUZAR DATOS DE ARTISTAS CON START AREA 1 Y 2 !!!!! Y DESPUES ASUMIR QUE CADA RELEASE TIENE SU ORIGEN DONDE SE PRODUCE. PASAR A NOTEBOOK DE GENERO